In [ ]:
# default_exp mining.ir

# Information Retrieval and Traceability Interfaces
> Implementing Common Information Retrieval Interfaces
> Author: @danaderp December 2020

We test diferent similarities based on [blog](https://www.kdnuggets.com/2017/08/comparing-distance-measurements-python-scipy.html) and [blog2](https://www.kdnuggets.com/2019/01/comparison-text-distance-metrics.html)

In [ ]:
# ! pip install -e . <----- Install in the console

In [ ]:
#export
import numpy as np
import gensim
import pandas as pd
from itertools import product 
from random import sample 
import functools 
import os

In [ ]:
#export
from gensim.models import WordEmbeddingSimilarityIndex
from gensim.similarities import SparseTermSimilarityMatrix
from gensim import corpora
from datetime import datetime
from enum import Enum, unique, auto
from ds4se.mgmnt.prep.conv import *

In [ ]:
#https://docs.scipy.org/doc/scipy/reference/generated/scipy.spatial.distance.cosine.html
#export
from scipy.spatial import distance
from scipy.stats import pearsonr

In [ ]:
#export
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

## Enums

In [ ]:
#export
#@unique
class VectorizationType(Enum):
    word2vec = auto()
    doc2vec = auto()
    vsm2vec = auto()

In [ ]:
VectorizationType.word2vec

<VectorizationType.word2vec: 1>

In [ ]:
#export
#@unique
class DistanceMetric(Enum):
    WMD = auto()
    COS = auto()
    SCM = auto()
    EUC = auto()
    MAN = auto()

In [ ]:
#export
#@unique
class SimilarityMetric(Enum):
    WMD_sim = auto()
    COS_sim = auto()
    SCM_sim = auto()
    EUC_sim = auto()
    MAN_sim = auto()
    Pearson = auto()

In [ ]:
#export
class EntropyMetric(Enum):
    MSI_I = auto() #Minimum shared information Entropy
    MSI_X = auto() #Minimum shared information Extropy
    MI = auto() #Mutual information
    JI = auto() #Joint information
    Loss = auto() #Conditioned Entropy given the output I(x|y)
    Noise = auto() #Conditioned Entropy given the input I(y|x)
    Entropy_src = auto() #Self  Information src artifacts
    Entropy_tgt = auto() #Self Information target artifacts

In [ ]:
#export
class SoftwareArtifacts(Enum):
    REQ = 'req'
    TC = 'tc'
    SRC = 'src'
    PY = 'py'
    PR = 'pr'

In [ ]:
#export
#@unique
class Preprocessing(Enum):
    conv = auto()
    bpe = auto()

In [ ]:
#export
#@unique
class LinkType(Enum):
    req2tc = auto()
    req2src = auto()
    issue2src = auto()
    pr2src = auto()

In [ ]:
#tst
LinkType.req2tc

<LinkType.req2tc: 1>

In [ ]:
#tst
Preprocessing.bpe

<Preprocessing.bpe: 2>

## 1. Setting-Up Testing Environment

In [ ]:
#hide
path_data = '../dvc-ds4se/' #dataset path

In [ ]:
#hide
#experiment 0.0.0
#check it out in https://docs.google.com/spreadsheets/d/1UggaKFK8Qr5YltG_X9dN9BUlgH-GNiAbfPkcqSxjyoo/edit?usp=sharing
path_to_trained_model = path_data+'models/wv/bpe8k/[word2vec-Java-Py-SK-500-20E-8k-1594090297.869643].model'
path_model_prefix = path_data+'models/bpe/sentencepiece/wiki_py_java_bpe_8k'

In [ ]:
#hide
#experiment 0.0.0
#Experiment 1 with Libest Conv preprocessing
def libest_params():
        return {
        "vectorizationType": VectorizationType.word2vec,
        "linkType": LinkType.req2tc,
        "system": 'libest',
        "path_to_trained_model": path_to_trained_model,
        "source_type": SoftwareArtifacts.REQ.value,
        "target_type": SoftwareArtifacts.TC.value,
        "system_path_config": {
            "system_path": path_data + 'se-benchmarking/traceability/cisco/libest_data/[libest-all-corpus-1596063103.098236].csv',
            "sep": '~',
            "names": ['ids','conv'],
            "prep": Preprocessing.conv
        },
        "saving_path": path_data + 'metrics/traceability/experiments0.0.x/',
        "names": ['Source','Target','Linked?'],
        "model_prefix":path_model_prefix, #For BPE Analysis
        "path_mappings": path_data + 'se-benchmarking/traceability/testbeds/groundtruth/english/[libest-ground-req-to-tc].txt',    
    }

In [ ]:
#hide
parameters = libest_params()
parameters

{'vectorizationType': <VectorizationType.word2vec: 1>,
 'linkType': <LinkType.req2tc: 1>,
 'system': 'libest',
 'path_to_trained_model': '../dvc-ds4se/models/wv/bpe8k/[word2vec-Java-Py-SK-500-20E-8k-1594090297.869643].model',
 'source_type': 'req',
 'target_type': 'tc',
 'system_path_config': {'system_path': '../dvc-ds4se/se-benchmarking/traceability/cisco/libest_data/[libest-all-corpus-1596063103.098236].csv',
  'sep': '~',
  'names': ['ids', 'conv'],
  'prep': <Preprocessing.conv: 1>},
 'saving_path': '../dvc-ds4se/metrics/traceability/experiments0.0.x/',
 'names': ['Source', 'Target', 'Linked?'],
 'model_prefix': '../dvc-ds4se/models/bpe/sentencepiece/wiki_py_java_bpe_8k',
 'path_mappings': '../dvc-ds4se/se-benchmarking/traceability/testbeds/groundtruth/english/[libest-ground-req-to-tc].txt'}

In [ ]:
parameters['source_type']

'req'

In [ ]:
#tst
parameters['system_path_config']['system_path']

'../dvc-ds4se/se-benchmarking/traceability/cisco/libest_data/[libest-all-corpus-1596063103.098236].csv'

In [ ]:
#tst
parameters['system_path_config']['names'][1]

'conv'

In [ ]:
parameters['system_path_config']['sep'] #tst

'~'

In [ ]:
#hide
df_all_system = pd.read_csv(
            parameters['system_path_config']['system_path'], 
            #names = params['system_path_config']['names'], #include the names into the files!!!
            header = 0, 
            index_col = 0, 
            sep = parameters['system_path_config']['sep'] 
        )

In [ ]:
df_all_system.head(1)

ids filenames  \
0  test_data/LibEST_semeru_format/test/us903.c   us903.c   

                                                text type  \
0  /*--------------------------------------------...   tc   

                                                conv  \
0  unit test user stori server simpl enrol august...   

                                             bpe128k  \
0  ['▁/*', '----------------', '----------------'...   

                                              bpe32k  \
0  ['▁/', '*', '--------', '--------', '--------'...   

                                               bpe8k  
0  ['▁/', '*', '-', '-', '-', '-', '-', '-', '-',...

In [ ]:
#hide
tag = parameters['system_path_config']['names'][1]
[doc.split() for doc in df_all_system[df_all_system[tag].notnull()][tag].values]

[['unit',
  'test',
  'user',
  'stori',
  'server',
  'simpl',
  'enrol',
  'august',
  'copyright',
  'cisco',
  'system',
  'inc',
  'right',
  'reserv',
  'includ',
  'stdio',
  'ifndef',
  'win',
  'includ',
  'unistd',
  'endif',
  'includ',
  'est',
  'includ',
  'curl',
  'curl',
  'includ',
  'curl',
  'util',
  'includ',
  'test',
  'util',
  'includ',
  'server',
  'includ',
  'openssl',
  'ssl',
  'ifdef',
  'cunit',
  'includ',
  'cunit',
  'basic',
  'includ',
  'cunit',
  'autom',
  'endif',
  'ifndef',
  'win',
  'static',
  'char',
  'test',
  'outfil',
  'filenam',
  'max',
  'test',
  'hdr',
  'defin',
  'cacert',
  'est',
  'cacert',
  'crt',
  'defin',
  'explicit_cert',
  'us903',
  'cert',
  'pem',
  'defin',
  'us903_explicit_key',
  'us903',
  'key',
  'pem',
  'defin',
  'us903_cacert',
  'est',
  'cacert',
  'crt',
  'defin',
  'us903_trusted_cert',
  'trustedcert',
  'crt',
  'defin',
  'est',
  'privat',
  'estservercertandkey',
  'pem',
  'els',
  'static'

In [ ]:
len(df_all_system[tag].values) #tst

87

In [ ]:
#tst
len(df_all_system[df_all_system[tag].notnull()]) #some files are _init_ thefore are empty

87

In [ ]:
#tst
df_all_system[df_all_system[tag].notnull()][tag].values

array(['unit test user stori server simpl enrol august copyright cisco system inc right reserv includ stdio ifndef win includ unistd endif includ est includ curl curl includ curl util includ test util includ server includ openssl ssl ifdef cunit includ cunit basic includ cunit autom endif ifndef win static char test outfil filenam max test hdr defin cacert est cacert crt defin explicit_cert us903 cert pem defin us903_explicit_key us903 key pem defin us903_cacert est cacert crt defin us903_trusted_cert trustedcert crt defin est privat estservercertandkey pem els static char test5_outfil filename_max us903 test5 hdr defin us903_cacert est cacert crt defin us903_explicit_cert us903 cert pem defin us903_explicit_key us903 key pem defin us903_cacert est cacert crt defin us903_trusted_cert trustedcert crt defin est privat estservercertandkey pem endif static unsign char cacert null static int cacerts_len defin us903_retry_interv 3600 defin us903_tcp_port 29001 follow csr generat use follow o

In [ ]:
#tst
df_all_system.loc[df_all_system['type'] == parameters['source_type']][parameters['system_path_config']['names']]

ids  \
35  test_data/LibEST_semeru_format/requirements/RQ...   
36  test_data/LibEST_semeru_format/requirements/RQ...   
37  test_data/LibEST_semeru_format/requirements/RQ...   
38  test_data/LibEST_semeru_format/requirements/RQ...   
39  test_data/LibEST_semeru_format/requirements/RQ...   
40  test_data/LibEST_semeru_format/requirements/RQ...   
41  test_data/LibEST_semeru_format/requirements/RQ...   
42  test_data/LibEST_semeru_format/requirements/RQ...   
43  test_data/LibEST_semeru_format/requirements/RQ...   
44  test_data/LibEST_semeru_format/requirements/RQ...   
45  test_data/LibEST_semeru_format/requirements/RQ...   
46  test_data/LibEST_semeru_format/requirements/RQ...   
47  test_data/LibEST_semeru_format/requirements/RQ...   
48  test_data/LibEST_semeru_format/requirements/RQ...   
49  test_data/LibEST_semeru_format/requirements/RQ...   
50  test_data/LibEST_semeru_format/requirements/RQ...   
51  test_data/LibEST_semeru_format/requirements/RQ...   
52  test_data/LibEST_semeru_format/requirements/RQ...   
53  test_data/LibEST_semeru_format/requirements/RQ...   
54  test_data/LibEST_semeru_format/requirements/RQ...   
55  test_data/LibEST_semeru_format/requirements/RQ...   
56  test_data/LibEST_semeru_format/requirements/RQ...   
57  test_data/LibEST_semeru_format/requirements/RQ...   
58  test_data/LibEST_semeru_format/requirements/RQ...   
59  test_data/LibEST_semeru_format/requirements/RQ...   
60  test_data/LibEST_semeru_format/requirements/RQ...   
61  test_data/LibEST_semeru_format/requirements/RQ...   
62  test_data/LibEST_semeru_format/requirements/RQ...   
63  test_data/LibEST_semeru_format/requirements/RQ...   
64  test_data/LibEST_semeru_format/requirements/RQ...   
65  test_data/LibEST_semeru_format/requirements/RQ...   
66  test_data/LibEST_semeru_format/requirements/RQ...   
67  test_data/LibEST_semeru_format/requirements/RQ...   
68  test_data/LibEST_semeru_format/requirements/RQ...   
69  test_data/LibEST_semeru_format/requirements/RQ...   
70  test_data/LibEST_semeru_format/requirements/RQ...   
71  test_data/LibEST_semeru_format/requirements/RQ...   
72  test_data/LibEST_semeru_format/requirements/RQ...   
73  test_data/LibEST_semeru_format/requirements/RQ...   
74  test_data/LibEST_semeru_format/requirements/RQ...   
75  test_data/LibEST_semeru_format/requirements/RQ...   
76  test_data/LibEST_semeru_format/requirements/RQ...   
77  test_data/LibEST_semeru_format/requirements/RQ...   
78  test_data/LibEST_semeru_format/requirements/RQ...   
79  test_data/LibEST_semeru_format/requirements/RQ...   
80  test_data/LibEST_semeru_format/requirements/RQ...   
81  test_data/LibEST_semeru_format/requirements/RQ...   
82  test_data/LibEST_semeru_format/requirements/RQ...   
83  test_data/LibEST_semeru_format/requirements/RQ...   
84  test_data/LibEST_semeru_format/requirements/RQ...   
85  test_data/LibEST_semeru_format/requirements/RQ...   
86  test_data/LibEST_semeru_format/requirements/RQ...   

                                                 conv  
35  requir http uri control est server must suppor...  
36  requir server side key generat respons request...  
37  requir http base client authent est server may...  
38  requir csr attribut request est client request...  
39  requir server side key generat est client may ...  
40  requir client author decis issu certif client ...  
41  requir csr attribut polici may allow inclus cl...  
42  requir simpl enrol client https post simpleenr...  
43  requir csr attribut follow exampl valid csratt...  
44  requir http layer http use transfer est messag...  
45  requir client certif request function est clie...  
46  requir secur consider support basic authent sp...  
47  requir server author client must check est ser...  
48  requir csr attribut respons local configur pol...  
49  requir server key generat est client request s...  
50  requir certif respons success server respons m...  
51  requir link ident pop inform server polici det...  
52  requir http head

In [ ]:
df_all_system.loc[df_all_system['type'] == parameters['target_type']][parameters['system_path_config']['names']]

ids  \
0    test_data/LibEST_semeru_format/test/us903.c   
1   test_data/LibEST_semeru_format/test/us3496.c   
2    test_data/LibEST_semeru_format/test/us899.c   
3   test_data/LibEST_semeru_format/test/us4020.c   
4    test_data/LibEST_semeru_format/test/us897.c   
5   test_data/LibEST_semeru_format/test/us1060.c   
6    test_data/LibEST_semeru_format/test/us900.c   
7    test_data/LibEST_semeru_format/test/us896.c   
8    test_data/LibEST_semeru_format/test/us894.c   
9   test_data/LibEST_semeru_format/test/us1005.c   
10   test_data/LibEST_semeru_format/test/us898.c   
11  test_data/LibEST_semeru_format/test/us3512.c   
12  test_data/LibEST_semeru_format/test/us1883.c   
13   test_data/LibEST_semeru_format/test/us748.c   
14  test_data/LibEST_semeru_format/test/us3612.c   
15   test_data/LibEST_semeru_format/test/us901.c   
16  test_data/LibEST_semeru_format/test/us1864.c   
17  test_data/LibEST_semeru_format/test/us1159.c   
18  test_data/LibEST_semeru_format/test/us2174.c   
19   test_data/LibEST_semeru_format/test/us893.c   
20   test_data/LibEST_semeru_format/test/us895.c   

                                                 conv  
0   unit test user stori server simpl enrol august...  
1   unit test uri path segment extens support marc...  
2   unit test user stori client simpl enrol septem...  
3   unit test user stori unit test client proxi mo...  
4   unit test user stori client cacert june copyri...  
5   unit test user stori tls srp support server pr...  
6   unit test user stori server csr attribut novem...  
7   unit test user stori client csr attribut novem...  
8   unit test user stori proxi cacert novemb copyr...  
9   unit test user stori client easi provis novemb...  
10  unit test user stori client enrol octob copyri...  
11  unit test uri path segment support server apri...  
12  unit test user stori enabl token auth mode est...  
13  unit test user stori proxi simpl enrol august ...  
14  unit test user stori encrypt privat key suppor...  
15  unit test user stori server cacert june copyri...  
16  unit test user stori enabl token auth mode ser...  
17  unit test user stori csr attribut enforc octob...  
18  unit test user stori proxi simpl enrol august ...  
19  unit test user stori proxi reenrol octob copyr...  
20  unit test user stori proxi csr attribut novemb...

## 1. Defining BasicSequenceVectorization

In [ ]:
#tst
print(list(VectorizationType), list(DistanceMetric), list(SimilarityMetric), list(LinkType))

[<VectorizationType.word2vec: 1>, <VectorizationType.doc2vec: 2>, <VectorizationType.vsm2vec: 3>] [<DistanceMetric.WMD: 1>, <DistanceMetric.COS: 2>, <DistanceMetric.SCM: 3>, <DistanceMetric.EUC: 4>, <DistanceMetric.MAN: 5>] [<SimilarityMetric.WMD_sim: 1>, <SimilarityMetric.COS_sim: 2>, <SimilarityMetric.SCM_sim: 3>, <SimilarityMetric.EUC_sim: 4>, <SimilarityMetric.MAN_sim: 5>, <SimilarityMetric.Pearson: 6>] [<LinkType.req2tc: 1>, <LinkType.req2src: 2>, <LinkType.issue2src: 3>, <LinkType.pr2src: 4>]


In [ ]:
#export
class BasicSequenceVectorization():
    '''Implementation of the class sequence-vanilla-vectorization other classes can inheritance this one'''
    def __init__(self, params):
                
        self.params = params
        self.df_nonground_link = None
        self.df_ground_link = None
        self.prep = ConventionalPreprocessing(self.params, bpe = True)
        
        self.df_all_system = pd.read_csv(
            self.params['system_path_config']['system_path'], 
            #names = params['system_path_config']['names'], #include the names into the files!!!
            header = 0, 
            index_col = 0, 
            sep = self.params['system_path_config']['sep'] 
        )
        
        #self.df_source = pd.read_csv(params['source_path'], names=['ids', 'text'], header=None, sep=' ')
        #self.df_target = pd.read_csv(params['target_path'], names=['ids', 'text'], header=None, sep=' ')
        self.df_source = self.df_all_system.loc[self.df_all_system['type'] == self.params['source_type']][self.params['system_path_config']['names']]
        self.df_target = self.df_all_system.loc[self.df_all_system['type'] == self.params['target_type']][self.params['system_path_config']['names']]
        
        #NA verification
        tag = self.params['system_path_config']['names'][1]
        self.df_source[tag] = self.df_source[tag].fillna("")
        self.df_target[tag] = self.df_target[tag].fillna("")
        
        ## self.document and self.dictionary is the vocabulary of the traceability corpus
        ## Do not confuse it with the dictionary of the general vectorization model
        if self.params['system_path_config']['prep'] == Preprocessing.conv: #if conventional preprocessing
            self.documents = [doc.split() for doc in self.df_all_system[self.df_all_system[tag].notnull()][tag].values] #Preparing Corpus
            self.dictionary = corpora.Dictionary( self.documents ) #Preparing Dictionary
            self.vocab = dict.fromkeys( self.dictionary.token2id.keys(),0 )
            logging.info("conventional preprocessing documents, dictionary, and vocab for the test corpus")
        
        elif self.params['system_path_config']['prep'] == Preprocessing.bpe:
            self.documents = [eval(doc) for doc in self.df_all_system[tag].values] #Preparing Corpus
            self.dictionary = corpora.Dictionary( self.documents ) #Preparing Dictionary
            self.computing_bpe_vocab()
            logging.info("bpe preprocessing documents, dictionary, and vocab for the test corpus")
        
        
        #This can be extended for future metrics <---------------------
        #TODO include mutual and join information
        self.dict_labels = {
            DistanceMetric.COS:[DistanceMetric.COS, SimilarityMetric.COS_sim],
            SimilarityMetric.Pearson:[SimilarityMetric.Pearson],
            DistanceMetric.EUC:[DistanceMetric.EUC, SimilarityMetric.EUC_sim],
            DistanceMetric.WMD:[DistanceMetric.WMD, SimilarityMetric.WMD_sim],
            DistanceMetric.SCM:[DistanceMetric.SCM, SimilarityMetric.SCM_sim],
            DistanceMetric.MAN:[DistanceMetric.MAN, SimilarityMetric.MAN_sim],
            EntropyMetric.MSI_I:[EntropyMetric.MSI_I, EntropyMetric.MSI_X],
            EntropyMetric.MI:[EntropyMetric.Entropy_src, EntropyMetric.Entropy_tgt,
                              EntropyMetric.JI, EntropyMetric.MI,
                              EntropyMetric.Loss, EntropyMetric.Noise
                             ]
        }

    def computing_bpe_vocab(self):
        ####INFO science params
        #TODO generalize bpe8k parameter
        abstracted_vocab = [ set(doc) for doc in self.df_all_system[ 'bpe8k' ].values] #creation of sets
        abstracted_vocab = functools.reduce( lambda a,b : a.union(b), abstracted_vocab ) #union of sets
        self.vocab = {self.prep.sp_bpe.id_to_piece(id): 0 for id in range(self.prep.sp_bpe.get_piece_size())}
        dict_abs_vocab = { elem : 0 for elem in abstracted_vocab - set(self.vocab.keys()) } #Ignored vocab by BPE
        self.vocab.update(dict_abs_vocab) #Updating
    
    def ground_truth_processing(self, path_to_ground_truth = '', from_mappings = False):
        'Optional class when corpus has ground truth. This function create tuples of links'
        
        if from_mappings:
            df_mapping = pd.read_csv(self.params['path_mappings'], header = 0, sep = ',')
            ground_links = list(zip(df_mapping['id_pr'].astype(str), df_mapping['doc_id']))
        else:
            ground_truth = open(path_to_ground_truth,'r')
            #Organizing The Ground Truth under the given format
            ground_links = [ [(line.strip().split()[0], elem) for elem in line.strip().split()[1:]] for line in ground_truth]
            ground_links = functools.reduce(lambda a,b : a+b,ground_links) #reducing into one list
            assert len(ground_links) ==  len(set(ground_links)) #To Verify Redundancies in the file
        return ground_links
    
    def samplingLinks(self, sampling = False, samples = 10, basename = False):
        
        if basename:
            source = [os.path.basename(elem) for elem in self.df_source['ids'].values ] 
            target = [os.path.basename(elem) for elem in self.df_target['ids'].values ]
        else:
            source = self.df_source['ids'].values
            target = self.df_target['ids'].values

        if sampling:
            links = sample( list( product( source , target ) ), samples)
        else:
            links = list( product( source , target ))

        return links
    
    def cos_scipy(self, vector_v, vector_w):
        cos =  distance.cosine( vector_v, vector_w )
        return [cos, 1.-cos]
    
    def euclidean_scipy(self, vector_v, vector_w):
        dst = distance.euclidean(vector_v,vector_w)
        return [dst, 1./(1.+dst)] #Computing the inverse for similarity
    
    def manhattan_scipy(self, vector_v, vector_w):
        dst = distance.cityblock(vector_v,vector_w)
        n = len(vector_v)
        return [dst, 1./(1.+dst)] #Computing the inverse for similarity
    
    def pearson_abs_scipy(self, vector_v, vector_w):
        '''We are not sure that pearson correlation works well on doc2vec inference vectors'''
        #vector_v =  np.asarray(vector_v, dtype=np.float32)
        #vector_w =  np.asarray(vector_w, dtype=np.float32)
        #logging.info("pearson_abs_scipy"  + 'len: ' + str(len(vector_v)) + 'type: ' + str(type(vector_v)) )
        #logging.info("pearson_abs_scipy"  + 'len: ' + str(len(vector_w)) + 'type: ' + str(type(vector_w)) )
        corr, _ = pearsonr(vector_v, vector_w)
        return [abs(corr)] #Absolute value of the correlation
    

    def computeDistanceMetric(self, links, metric_list):
        '''Metric List Iteration''' 
        
        metric_labels = [ self.dict_labels[metric] for metric in metric_list] #tracking of the labels
        distSim = [[link[0], link[1], self.distance( metric_list, link )] for link in links] #Return the link with metrics
        distSim = [[elem[0], elem[1]] + elem[2] for elem in distSim] #Return the link with metrics
        
        return distSim, functools.reduce(lambda a,b : a+b, metric_labels)
    
    def ComputeDistanceArtifacts(self, metric_list, sampling = False , samples = 10, basename = False):
        '''Activates Distance and Similarity Computations
        @metric_list if [] then Computes All metrics
        @sampling is False by the default
        @samples is the number of samples (or links) to be generated'''
        links_ = self.samplingLinks( sampling, samples, basename )
        
        docs, metric_labels = self.computeDistanceMetric( metric_list=metric_list, links=links_) #checkpoints
        self.df_nonground_link = pd.DataFrame(docs, columns =[self.params['names'][0], self.params['names'][1]]+ metric_labels) #Transforming into a Pandas
        logging.info("Non-groundtruth links computed")
        pass 
    
    
    def SaveLinks(self, grtruth=False, sep=' ', mode='a'):
        timestamp = datetime.timestamp(datetime.now())
        path_to_link = self.params['saving_path'] + '['+ self.params['system'] + '-' + str(self.params['vectorizationType']) + '-' + str(self.params['linkType']) + '-' + str(grtruth) + '-{}].csv'.format(timestamp)
        
        if grtruth:
            self.df_ground_link.to_csv(path_to_link, header=True, index=True, sep=sep, mode=mode)
        else:
            self.df_nonground_link.to_csv(path_to_link, header=True, index=True, sep=sep, mode=mode)
        
        logging.info('Saving in...' + path_to_link)
        pass
    
    def findDistInDF(self, g_tuple, from_mappings=False, semeru_format=False):
        '''Return the index values of the matched mappings
        .eq is used for Source since it must match the exact code to avoid number substrings
        for the target, the substring might works fine'''

        if from_mappings: #SACP Format
            dist = self.df_ground_link.loc[(self.df_ground_link["Source"].eq(g_tuple[0]) ) & 
                 (self.df_ground_link["Target"].str.contains(g_tuple[1], regex=False))]
            logging.info('findDistInDF: from_mappings')
        elif semeru_format: #LibEST Format
            dist = self.df_ground_link.loc[(self.df_ground_link["Source"].str.contains(g_tuple[0], regex=False) ) & 
                 (self.df_ground_link["Target"].str.contains(g_tuple[1], regex=False))]
            logging.info('findDistInDF: semeru_format')
        else: #By Default use Semeru Format
            dist = self.df_ground_link[self.df_ground_link[self.params['names'][0]].str.contains( g_tuple[0][:g_tuple[0].find('.')] + '-' ) 
                     & self.df_ground_link[self.params['names'][1]].str.contains(g_tuple[1][:g_tuple[1].find('.')]) ]
            logging.info('findDistInDF: default')
        return dist.index.values
    
        
    def MatchWithGroundTruth(self, path_to_ground_truth='', from_mappings=False, semeru_format=False ):
        self.df_ground_link = self.df_nonground_link.copy()
        self.df_ground_link[self.params['names'][2]] = 0
        
        matchGT = [ self.findDistInDF( g , from_mappings=from_mappings, semeru_format=semeru_format ) for g in self.ground_truth_processing(path_to_ground_truth,from_mappings)]
        matchGT = functools.reduce(lambda a,b : np.concatenate([a,b]), matchGT) #Concatenate indexes
        new_column = pd.Series(np.full([len(matchGT)], 1 ), name=self.params['names'][2], index = matchGT)
        
        self.df_ground_link.update(new_column)
        logging.info("Groundtruth links computed")
        pass

### Testing BasicSequenceVectorization

In [ ]:
general2vec =  BasicSequenceVectorization(params = parameters)

2020-12-19 00:51:51,902 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 00:51:51,959 : INFO : built Dictionary(6957 unique tokens: ['");', '"../../', '("\\', '();', ')))']...) from 87 documents (total 88944 corpus positions)
2020-12-19 00:51:51,961 : INFO : conventional preprocessing documents, dictionary, and vocab for the test corpus


In [ ]:
m = dict.fromkeys( general2vec.dictionary.token2id.keys(),0 ) #From traceability dataset!

In [ ]:
n = general2vec.vocab

In [ ]:
len(set(m.keys()) - set(n.keys())) #TODO

0

In [ ]:
assert len(set( m.keys()) - set(n.keys())) == 0 

In [ ]:
general2vec.documents

[['unit',
  'test',
  'user',
  'stori',
  'server',
  'simpl',
  'enrol',
  'august',
  'copyright',
  'cisco',
  'system',
  'inc',
  'right',
  'reserv',
  'includ',
  'stdio',
  'ifndef',
  'win',
  'includ',
  'unistd',
  'endif',
  'includ',
  'est',
  'includ',
  'curl',
  'curl',
  'includ',
  'curl',
  'util',
  'includ',
  'test',
  'util',
  'includ',
  'server',
  'includ',
  'openssl',
  'ssl',
  'ifdef',
  'cunit',
  'includ',
  'cunit',
  'basic',
  'includ',
  'cunit',
  'autom',
  'endif',
  'ifndef',
  'win',
  'static',
  'char',
  'test',
  'outfil',
  'filenam',
  'max',
  'test',
  'hdr',
  'defin',
  'cacert',
  'est',
  'cacert',
  'crt',
  'defin',
  'explicit_cert',
  'us903',
  'cert',
  'pem',
  'defin',
  'us903_explicit_key',
  'us903',
  'key',
  'pem',
  'defin',
  'us903_cacert',
  'est',
  'cacert',
  'crt',
  'defin',
  'us903_trusted_cert',
  'trustedcert',
  'crt',
  'defin',
  'est',
  'privat',
  'estservercertandkey',
  'pem',
  'els',
  'static'

In [ ]:
len(general2vec.dictionary)

6957

In [ ]:
general2vec.dictionary

In [ ]:
general2vec.df_all_system.head(1)

ids filenames  \
0  test_data/LibEST_semeru_format/test/us903.c   us903.c   

                                                text type  \
0  /*--------------------------------------------...   tc   

                                                conv  \
0  unit test user stori server simpl enrol august...   

                                             bpe128k  \
0  ['▁/*', '----------------', '----------------'...   

                                              bpe32k  \
0  ['▁/', '*', '--------', '--------', '--------'...   

                                               bpe8k  
0  ['▁/', '*', '-', '-', '-', '-', '-', '-', '-',...

In [ ]:
general2vec.df_all_system.shape #data final tensor

(87, 8)

In [ ]:
#tst for libest
path_to_ground_truth = parameters['path_mappings']
general2vec.ground_truth_processing(path_to_ground_truth)

[('RQ4.txt', 'us1864.c'),
 ('RQ4.txt', 'us901.c'),
 ('RQ4.txt', 'us1005.c'),
 ('RQ4.txt', 'us3512.c'),
 ('RQ4.txt', 'us895.c'),
 ('RQ4.txt', 'us897.c'),
 ('RQ4.txt', 'us900.c'),
 ('RQ6.txt', 'us1005.c'),
 ('RQ6.txt', 'us1159.c'),
 ('RQ6.txt', 'us3496.c'),
 ('RQ6.txt', 'us3512.c'),
 ('RQ6.txt', 'us3612.c'),
 ('RQ6.txt', 'us4020.c'),
 ('RQ6.txt', 'us748.c'),
 ('RQ6.txt', 'us893.c'),
 ('RQ6.txt', 'us895.c'),
 ('RQ6.txt', 'us896.c'),
 ('RQ6.txt', 'us897.c'),
 ('RQ6.txt', 'us898.c'),
 ('RQ6.txt', 'us899.c'),
 ('RQ6.txt', 'us900.c'),
 ('RQ8.txt', 'us1005.c'),
 ('RQ8.txt', 'us1159.c'),
 ('RQ8.txt', 'us1883.c'),
 ('RQ8.txt', 'us2174.c'),
 ('RQ8.txt', 'us3496.c'),
 ('RQ8.txt', 'us3512.c'),
 ('RQ8.txt', 'us3612.c'),
 ('RQ8.txt', 'us4020.c'),
 ('RQ8.txt', 'us748.c'),
 ('RQ8.txt', 'us893.c'),
 ('RQ8.txt', 'us895.c'),
 ('RQ8.txt', 'us896.c'),
 ('RQ8.txt', 'us897.c'),
 ('RQ8.txt', 'us898.c'),
 ('RQ8.txt', 'us899.c'),
 ('RQ8.txt', 'us900.c'),
 ('RQ11.txt', 'us1159.c'),
 ('RQ11.txt', 'us1883.c'),
 ('R

In [ ]:
#tst for sacp <----- Warning!
#general2vec.ground_truth_processing(parameters['path_mappings'], from_mappings = True)

## 2. Artifacts Similarity with Word2Vec

In [ ]:
#export
from collections import Counter
import dit
import math

In [ ]:
#export
class Word2VecSeqVect(BasicSequenceVectorization):       
    
    def __init__(self, params):
        super().__init__(params)
        self.new_model = gensim.models.Word2Vec.load( params['path_to_trained_model'] )
        self.new_model.init_sims(replace=True)  # Normalizes the vectors in the word2vec class.
        #Computes cosine similarities between word embeddings and retrieves the closest 
        #word embeddings by cosine similarity for a given word embedding.
        self.similarity_index = WordEmbeddingSimilarityIndex(self.new_model.wv)
        #Build a term similarity matrix and compute the Soft Cosine Measure.
        self.similarity_matrix = SparseTermSimilarityMatrix(self.similarity_index, self.dictionary)
        
        self.dict_distance_dispatcher = {
            DistanceMetric.COS: self.cos_scipy,
            SimilarityMetric.Pearson: self.pearson_abs_scipy,
            DistanceMetric.WMD: self.wmd_gensim,
            DistanceMetric.SCM: self.scm_gensim,
            EntropyMetric.MSI_I: self.msi,
            EntropyMetric.MI: self.mutual_info
        }
    
    def wmd_gensim(self, sentence_a, sentence_b ):
        wmd = self.new_model.wv.wmdistance(sentence_a, sentence_b)
        return [wmd, self.wmd_similarity(wmd)]
    
    def wmd_similarity(self, dist):
        return 1./( 1.+float( dist ) ) #Associated Similarity
    
    def scm_gensim(self, sentence_a, sentence_b ):
        '''Compute SoftCosine Similarity of Gensim'''
        #Convert the sentences into bag-of-words vectors.
        sentence_1 = self.dictionary.doc2bow(sentence_a)
        sentence_2 = self.dictionary.doc2bow(sentence_b)
        
        #Return the inner product(s) between real vectors / corpora vec1 and vec2 expressed in a non-orthogonal normalized basis,
        #where the dot product between the basis vectors is given by the sparse term similarity matrix.
        scm_similarity = self.similarity_matrix.inner_product(sentence_1, sentence_2, normalized=True)
        return [1-scm_similarity, scm_similarity]
    
    def msi(self, sentence_a, sentence_b):
        '''@danaderp
        Minimum Shared Information'''
        vocab = self.vocab.copy()
        token_counts_1 = self.__get_cnts(sentence_a, vocab)
        token_counts_2 = self.__get_cnts(sentence_b, vocab)
        logging.info('token count processed')
        #Minimum Shared Tokens
        #TODO create an if down to include Joint Entropy by summing token_counts_1 and token_counts_2
        token_counts = { token: min(token_counts_1[token],token_counts_2[token]) for token in vocab }
        
        alphabet = list(set(token_counts.keys())) #[ list(set(cnt.keys())) for cnt in token_counts ]
        frequencies = self.__get_freqs(token_counts) #[ get_freqs(cnt) for cnt in token_counts ]
        logging.info('frequencies processed')
            
        if not frequencies:
            #"List is empty"
            entropies = float('nan')
            extropies = float('nan')
        else:
            scalar_distribution = dit.ScalarDistribution(alphabet, frequencies) #[dit.ScalarDistribution(alphabet[id], frequencies[id]) for id in range( len(token_counts) )]
            logging.info('scalar_distribution processed')
            
            entropies = dit.shannon.entropy( scalar_distribution ) #[ dit.shannon.entropy( dist ) for dist in scalar_distribution ]
            logging.info('entropies processed')
            
            extropies = dit.other.extropy( scalar_distribution )# [ dit.other.extropy( dist ) for dist in scalar_distribution ]
            logging.info('extropies processed')
        return [entropies,extropies]
    
    def mutual_info(self, sentence_a, sentence_b):
        """ Computing the manifold of metric of information
        Mutual information 
        Joint Information
        Conditioned Information Loss
        Conditioned Information Noise
        Self-Information
        """
        vocab = self.vocab.copy()
        token_counts_1 = self.__get_cnts(sentence_a, vocab)
        token_counts_2 = self.__get_cnts(sentence_b, vocab)
        logging.info('token count processed')


        #TODO verify redundancies in the alphabet
        alphabet_source = list(set(token_counts_1.keys()))
        logging.info('alphabet_source #'+ str(len(alphabet_source)))
        alphabet_target = list(set(token_counts_2.keys()))
        logging.info('alphabet_target #'+ str(len(alphabet_target)))
        
        logging.info('vocab #'+ str(len(self.vocab.keys())))
        logging.info('diff #'+ str(set(token_counts_1.keys()) - set(token_counts_2.keys())))
        #Computing Self-Information (or Entropy)
        scalar_distribution_source = dit.ScalarDistribution(alphabet_source, self.__get_freqs( token_counts_1 ) )
        entropy_source = dit.shannon.entropy( scalar_distribution_source )
        
        scalar_distribution_target = dit.ScalarDistribution(alphabet_target, self.__get_freqs( token_counts_2 ) )
        entropy_target = dit.shannon.entropy( scalar_distribution_target )
        
        #Computing Joint-information
        token_counts = { token: (token_counts_1[token] + token_counts_2[token]) for token in vocab }
        alphabet = list(set(token_counts.keys()))
        logging.info('alphabet #'+ str(len(alphabet)))
        frequencies = self.__get_freqs(token_counts)
        ##WARNING! if a document is empty frequencies might create an issue!
        scalar_distribution = dit.ScalarDistribution(alphabet, frequencies)
        joint_entropy = dit.shannon.entropy( scalar_distribution )
        
        #Computing Mutual-Information
        mutual_information = entropy_source + entropy_target - joint_entropy
        
        #Computing Noise
        noise = joint_entropy - entropy_target
        
        #Computing Loss
        loss = joint_entropy - entropy_source
        
        return [entropy_source, entropy_target, joint_entropy, 
                mutual_information, loss, noise]
    
    #ToDo Mutual information
    
    def distance(self, metric_list,link):
        '''Iterate on the metrics'''
        #Computation of sentences can be moved directly to wmd_gensim method if we cannot generalize it for 
        #the remaining metrics
        ids = self.params['system_path_config']['names'][0]
        txt = self.params['system_path_config']['names'][1]
        
        if self.params['system_path_config']['prep'] == Preprocessing.conv: #if conventional preprocessing
            sentence_a = self.df_source[self.df_source[ids].str.contains(link[0])][txt].values[0].split()
            sentence_b = self.df_target[self.df_target[ids].str.contains(link[1])][txt].values[0].split()
        elif self.params['system_path_config']['prep'] == Preprocessing.bpe:
            sentence_a = eval(self.df_source[self.df_source[ids].str.contains(link[0])][txt].values[0])
            sentence_b = eval(self.df_target[self.df_target[ids].str.contains(link[1])][txt].values[0])
        
        dist = [ self.dict_distance_dispatcher[metric](sentence_a,sentence_b) for metric in metric_list]
        logging.info("Computed distances or similarities "+ str(link) + str(dist))    
        return functools.reduce(lambda a,b : a+b, dist) #Always return a list
    
    #################################3TODO substitute this block in the future by importing information science module
    def __get_cnts(self, toks, vocab):
        '''@danaderp
        Counts tokens within ONE document'''
        #logging.info("encoding_size:" len
        cnt = Counter(vocab)
        for tok in toks:
            cnt[tok] += 1
        return cnt

    def __get_freqs(self, dict_token_counts):

        num_tokens = sum( dict_token_counts.values() ) #number of subwords inside the document
        if num_tokens == 0.0:
            frequencies = []
            logging.info('---------------> NO SHARED INFORMATION <-------------------------')
        else:
            frequencies = [ (dict_token_counts[token])/num_tokens for token in dict_token_counts ]
        return frequencies
    #################################3


In [ ]:
#export
def LoadLinks(timestamp, params, grtruth=False, sep=' ' ):
    '''Returns a pandas from a saved link computation at a give timestamp
    @timestamp is the version of the model for a given system'''
    
    path= params['saving_path'] + '['+ params['system'] + '-' + str(params['vectorizationType']) + '-' + str(params['linkType']) + '-' + str(grtruth) + '-{}].csv'.format(timestamp)
    
    logging.info("Loading computed links from... "+ path)

    return pd.read_csv(path, header=0, index_col=0, sep=sep)

### Testing Word2Vec SequenceVectorization

In [ ]:
#hide
#tst
metric_list = ['a','b']
A = [[1,3,4],[4,5],[1,8,9,7]]
B = ((1,3,4),(4,5),(1,8,9,7))
functools.reduce(lambda a,b : a+b, B)
dist_sim_T = [([12,13],['metric1','metric2']),([12,13],['metric1','metric2'])]
dist_sim_T
separated_merged_list_a = functools.reduce(lambda a,b : a[1]+b[1], dist_sim_T)
separated_merged_list_a

In [ ]:
#[step 1]Creating the Vectorization Class
word2vec = Word2VecSeqVect( params = parameters )

2020-12-19 00:52:11,849 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 00:52:11,905 : INFO : built Dictionary(6957 unique tokens: ['");', '"../../', '("\\', '();', ')))']...) from 87 documents (total 88944 corpus positions)
2020-12-19 00:52:11,906 : INFO : conventional preprocessing documents, dictionary, and vocab for the test corpus
2020-12-19 00:52:11,907 : INFO : loading Word2Vec object from ../dvc-ds4se/models/wv/bpe8k/[word2vec-Java-Py-SK-500-20E-8k-1594090297.869643].model
2020-12-19 00:52:12,357 : INFO : loading wv recursively from ../dvc-ds4se/models/wv/bpe8k/[word2vec-Java-Py-SK-500-20E-8k-1594090297.869643].model.wv.* with mmap=None
2020-12-19 00:52:12,358 : INFO : setting ignored attribute vectors_norm to None
2020-12-19 00:52:12,360 : INFO : loading vocabulary recursively from ../dvc-ds4se/models/wv/bpe8k/[word2vec-Java-Py-SK-500-20E-8k-1594090297.869643].model.vocabulary.* with mmap=None
2020-12-19 00:52:12,361 : INFO : loading trainables recurs

In [ ]:
len(word2vec.new_model.wv.vocab)

7888

In [ ]:
word2vec.df_source['ids'][35]

'test_data/LibEST_semeru_format/requirements/RQ17.txt'

In [ ]:
word2vec.df_source['ids'][35] #In LIBEST REQ starts at 35

'test_data/LibEST_semeru_format/requirements/RQ17.txt'

In [ ]:
ids = parameters['system_path_config']['names'][0]
txt = parameters['system_path_config']['names'][1]
print(ids,txt)

ids conv


In [ ]:
idss = word2vec.df_source[ids][35] #Selecting an ID
idss = word2vec.df_source[ids] == idss #Search for an specific ID
list(word2vec.df_source[idss][txt])[0].split() #Retrieving text and splitting

['requir',
 'http',
 'uri',
 'control',
 'est',
 'server',
 'must',
 'support',
 'use',
 'path',
 'prefix',
 'well',
 'known',
 'defin',
 'rfc',
 'regist',
 'name',
 'est',
 'thus',
 'valid',
 'est',
 'server',
 'uri',
 'path',
 'begin',
 'https',
 'www',
 'exampl',
 'com',
 'well',
 'known',
 'est',
 'est',
 'oper',
 'indic',
 'path',
 'suffix',
 'indic',
 'intend',
 'oper',
 'oper',
 'correspond',
 'uri',
 'oper',
 'oper',
 'path',
 'detail',
 'distribut',
 'cacert',
 'section',
 'certif',
 'must',
 'enrol',
 'simpleenrol',
 'section',
 'client',
 'must',
 'enrol',
 'simplereenrol',
 'section',
 'client',
 'must',
 'full',
 'cmc',
 'option',
 'fullcmc',
 'section',
 'server',
 'side',
 'key',
 'serverkeygen',
 'section',
 'generat',
 'option',
 'csr',
 'attribut',
 'csrattr',
 'section',
 'option',
 'figur',
 'oper',
 'path',
 'figur',
 'append',
 'path',
 'prefix',
 'form',
 'uri',
 'use',
 'http',
 'get',
 'post',
 'perform',
 'desir',
 'est',
 'oper',
 'exampl',
 'valid',
 'uri',


In [ ]:
word2vec.df_source.head(2)

ids  \
35  test_data/LibEST_semeru_format/requirements/RQ...   
36  test_data/LibEST_semeru_format/requirements/RQ...   

                                                 conv  
35  requir http uri control est server must suppor...  
36  requir server side key generat respons request...

In [ ]:
word2vec.df_target.head(2)

ids  \
0   test_data/LibEST_semeru_format/test/us903.c   
1  test_data/LibEST_semeru_format/test/us3496.c   

                                                conv  
0  unit test user stori server simpl enrol august...  
1  unit test uri path segment extens support marc...

In [ ]:
links = word2vec.samplingLinks(sampling=True, samples = 2)
links

[('test_data/LibEST_semeru_format/requirements/RQ35.txt',
  'test_data/LibEST_semeru_format/test/us3496.c'),
 ('test_data/LibEST_semeru_format/requirements/RQ28.txt',
  'test_data/LibEST_semeru_format/test/us3612.c')]

In [ ]:
print( len(links), word2vec.df_source.shape, word2vec.df_target.shape )

2 (52, 2) (21, 2)


In [ ]:
links[0][0]

'test_data/LibEST_semeru_format/requirements/RQ35.txt'

In [ ]:
#tst
word2vec.df_source[word2vec.df_source[ids].str.contains(links[0][0])][txt].values[0].split() #conventioanal
#eval(word2vec.df_source[word2vec.df_source[ids].str.contains(links[0][0])][txt].values[0]) #BPE

['requir',
 'client',
 'certif',
 'request',
 'function',
 'est',
 'client',
 'request',
 'certif',
 'est',
 'server',
 'https',
 'post',
 'use',
 'oper',
 'path',
 'valu',
 'simpleenrol',
 'est',
 'client',
 'request',
 'renew',
 'rekey',
 'exist',
 'certif',
 'http',
 'post',
 'use',
 'oper',
 'path',
 'valu',
 'simplereenrol',
 'est',
 'server',
 'must',
 'support',
 'simpleenrol',
 'simplereenrol',
 'function',
 'recommend',
 'client',
 'obtain',
 'current',
 'certif',
 'describ',
 'section',
 'perform',
 'certif',
 'request',
 'function',
 'ensur',
 'client',
 'abl',
 'valid',
 'est',
 'server',
 'certif',
 'client',
 'must',
 'authent',
 'est',
 'server',
 'specifi',
 'section',
 'certif',
 'base',
 'authent',
 'use',
 'section',
 'option',
 'certif',
 'less',
 'authent',
 'use',
 'client',
 'must',
 'verifi',
 'author',
 'est',
 'server',
 'specifi',
 'section',
 'server',
 'must',
 'authent',
 'client',
 'specifi',
 'section',
 'certif',
 'base',
 'authent',
 'use',
 'section',

In [ ]:
#tst
word2vec.df_target[word2vec.df_target[ids].str.contains(links[0][1])][txt].values[0].split()

['unit',
 'test',
 'uri',
 'path',
 'segment',
 'extens',
 'support',
 'march',
 'copyright',
 'cisco',
 'system',
 'inc',
 'right',
 'reserv',
 'includ',
 'stdio',
 'ifndef',
 'win',
 'includ',
 'unistd',
 'endif',
 'includ',
 'est',
 'includ',
 'curl',
 'curl',
 'includ',
 'curl',
 'util',
 'ifdef',
 'cunit',
 'includ',
 'cunit',
 'basic',
 'includ',
 'cunit',
 'autom',
 'endif',
 'includ',
 'util',
 'test',
 'util',
 'includ',
 'server',
 'includ',
 'src',
 'est',
 'est',
 'locl',
 'extern',
 'char',
 'tst',
 'srvr',
 'path',
 'seg',
 'enrol',
 'extern',
 'char',
 'tst',
 'srvr',
 'path',
 'seg',
 'auth',
 'static',
 'int',
 'path',
 'segment',
 'support',
 'max',
 'command',
 'line',
 'length',
 'generat',
 'system',
 'command',
 'defin',
 'est',
 'max',
 'cmd_len',
 '256',
 'certif',
 'use',
 'verifi',
 'est',
 'server',
 'grab',
 'server',
 'directori',
 'defin',
 'client_ut_cacert',
 '"../../',
 'exampl',
 'server',
 'est',
 'cacert',
 'crt',
 'defin',
 'client_ut_cacert',
 'est

In [ ]:
metric_list = [DistanceMetric.WMD,DistanceMetric.SCM,EntropyMetric.MSI_I,EntropyMetric.MI]
#metric_list = [EntropyMetric.MSI_I,EntropyMetric.MI]

In [ ]:
#[optional] computeDistanceMetric Testing [WARNING!] Time Consuming!!
computeDistanceMetric = word2vec.computeDistanceMetric(links, metric_list = metric_list )
computeDistanceMetric

2020-12-19 00:53:03,994 : INFO : Removed 110 and 1487 OOV words from document 1 and 2 (respectively).
2020-12-19 00:53:03,996 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 00:53:03,997 : INFO : built Dictionary(32 unique tokens: ['base', 'est', 'less', 'may', 'one']...) from 2 documents (total 250 corpus positions)
2020-12-19 00:53:04,012 : INFO : token count processed
2020-12-19 00:53:04,018 : INFO : frequencies processed
2020-12-19 00:53:04,652 : INFO : scalar_distribution processed
2020-12-19 00:53:04,653 : INFO : entropies processed
2020-12-19 00:53:04,654 : INFO : extropies processed
2020-12-19 00:53:04,657 : INFO : token count processed
2020-12-19 00:53:04,658 : INFO : alphabet_source #6957
2020-12-19 00:53:04,659 : INFO : alphabet_target #6957
2020-12-19 00:53:04,660 : INFO : vocab #6957
2020-12-19 00:53:04,662 : INFO : diff #set()
2020-12-19 00:53:05,899 : INFO : alphabet #6957
2020-12-19 00:53:06,515 : INFO : Computed distances or similarities ('tes

([['test_data/LibEST_semeru_format/requirements/RQ35.txt',
   'test_data/LibEST_semeru_format/test/us3496.c',
   1.0365468004777898,
   0.4910272623076436,
   0.8108923137187958,
   0.18910769,
   3.475098311604626,
   1.355589451724954,
   5.0288078800464975,
   7.2878904389256105,
   7.401793526889205,
   4.914904792082903,
   2.3729856468427073,
   0.11390308796359427],
  ['test_data/LibEST_semeru_format/requirements/RQ28.txt',
   'test_data/LibEST_semeru_format/test/us3612.c',
   1.0571186696703938,
   0.4861168267751063,
   0.8713501840829849,
   0.12864982,
   3.00623892865339,
   1.3374329493342525,
   4.6420846845805,
   7.345352443618291,
   7.429494794299984,
   4.557942333898808,
   2.7874101097194837,
   0.0841423506816934]],
 [<DistanceMetric.WMD: 1>,
  <SimilarityMetric.WMD_sim: 1>,
  <DistanceMetric.SCM: 3>,
  <SimilarityMetric.SCM_sim: 3>,
  <EntropyMetric.MSI_I: 1>,
  <EntropyMetric.MSI_X: 2>,
  <EntropyMetric.Entropy_src: 7>,
  <EntropyMetric.Entropy_tgt: 8>,
  <Entro

In [ ]:
#[step 2]NonGroundTruth Computation
word2vec.ComputeDistanceArtifacts( sampling=False, samples = 5, metric_list = metric_list )
word2vec.df_nonground_link.head()

2020-12-19 00:53:22,170 : INFO : Removed 172 and 1761 OOV words from document 1 and 2 (respectively).
2020-12-19 00:53:22,171 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 00:53:22,173 : INFO : built Dictionary(44 unique tokens: ['://', 'com', 'est', 'form', 'get']...) from 2 documents (total 245 corpus positions)
2020-12-19 00:53:22,200 : INFO : token count processed
2020-12-19 00:53:22,209 : INFO : frequencies processed
2020-12-19 00:53:22,849 : INFO : scalar_distribution processed
2020-12-19 00:53:22,850 : INFO : entropies processed
2020-12-19 00:53:22,851 : INFO : extropies processed
2020-12-19 00:53:22,853 : INFO : token count processed
2020-12-19 00:53:22,855 : INFO : alphabet_source #6957
2020-12-19 00:53:22,856 : INFO : alphabet_target #6957
2020-12-19 00:53:22,857 : INFO : vocab #6957
2020-12-19 00:53:22,859 : INFO : diff #set()
2020-12-19 00:53:24,102 : INFO : alphabet #6957
2020-12-19 00:53:24,718 : INFO : Computed distances or similarities ('test

2020-12-19 00:53:37,522 : INFO : token count processed
2020-12-19 00:53:37,529 : INFO : frequencies processed
2020-12-19 00:53:38,153 : INFO : scalar_distribution processed
2020-12-19 00:53:38,154 : INFO : entropies processed
2020-12-19 00:53:38,155 : INFO : extropies processed
2020-12-19 00:53:38,160 : INFO : token count processed
2020-12-19 00:53:38,162 : INFO : alphabet_source #6957
2020-12-19 00:53:38,164 : INFO : alphabet_target #6957
2020-12-19 00:53:38,165 : INFO : vocab #6957
2020-12-19 00:53:38,168 : INFO : diff #set()
2020-12-19 00:53:39,413 : INFO : alphabet #6957
2020-12-19 00:53:40,030 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ17.txt', 'test_data/LibEST_semeru_format/test/us900.c')[[1.021296649080398, 0.49473193380840785], [0.939129114151001, 0.060870886], [3.7277573751069215, 1.3437088691066412], [6.0246745048551915, 7.127980212598745, 7.403072733067834, 5.7495819843861025, 1.3783982282126424, 0.27509252046908905]]
2020-12

2020-12-19 00:53:53,543 : INFO : extropies processed
2020-12-19 00:53:53,546 : INFO : token count processed
2020-12-19 00:53:53,547 : INFO : alphabet_source #6957
2020-12-19 00:53:53,548 : INFO : alphabet_target #6957
2020-12-19 00:53:53,549 : INFO : vocab #6957
2020-12-19 00:53:53,551 : INFO : diff #set()
2020-12-19 00:53:54,793 : INFO : alphabet #6957
2020-12-19 00:53:55,423 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ17.txt', 'test_data/LibEST_semeru_format/test/us1883.c')[[0.9174282265917624, 0.5215319072346738], [0.7270097732543945, 0.27299023], [4.824116405014095, 1.4020498971400284], [6.0246745048551915, 9.006525301292756, 9.060589959535656, 5.970609846612291, 3.035915454680465, 0.05406465824290052]]
2020-12-19 00:53:55,426 : INFO : Removed 172 and 1726 OOV words from document 1 and 2 (respectively).
2020-12-19 00:53:55,427 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 00:53:55,429 : INFO : built Diction

2020-12-19 00:54:08,861 : INFO : vocab #6957
2020-12-19 00:54:08,862 : INFO : diff #set()
2020-12-19 00:54:10,111 : INFO : alphabet #6957
2020-12-19 00:54:10,727 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ17.txt', 'test_data/LibEST_semeru_format/test/us2174.c')[[0.866200398870977, 0.5358481332470966], [0.7431217133998871, 0.2568783], [4.489963579885211, 1.3876211312696747], [6.0246745048551915, 9.228957519717383, 9.276886157150905, 5.97674586742167, 3.2522116522957134, 0.047928637433521715]]
2020-12-19 00:54:10,731 : INFO : Removed 172 and 2212 OOV words from document 1 and 2 (respectively).
2020-12-19 00:54:10,731 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 00:54:10,732 : INFO : built Dictionary(50 unique tokens: ['://', 'com', 'est', 'form', 'get']...) from 2 documents (total 335 corpus positions)
2020-12-19 00:54:10,753 : INFO : token count processed
2020-12-19 00:54:10,758 : INFO : frequencies processed


2020-12-19 00:54:26,073 : INFO : Removed 322 and 2273 OOV words from document 1 and 2 (respectively).
2020-12-19 00:54:26,074 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 00:54:26,076 : INFO : built Dictionary(43 unique tokens: ['associ', 'base', 'der', 'est', 'field']...) from 2 documents (total 431 corpus positions)
2020-12-19 00:54:26,106 : INFO : token count processed
2020-12-19 00:54:26,113 : INFO : frequencies processed
2020-12-19 00:54:26,731 : INFO : scalar_distribution processed
2020-12-19 00:54:26,732 : INFO : entropies processed
2020-12-19 00:54:26,733 : INFO : extropies processed
2020-12-19 00:54:26,736 : INFO : token count processed
2020-12-19 00:54:26,737 : INFO : alphabet_source #6957
2020-12-19 00:54:26,739 : INFO : alphabet_target #6957
2020-12-19 00:54:26,739 : INFO : vocab #6957
2020-12-19 00:54:26,741 : INFO : diff #set()
2020-12-19 00:54:27,981 : INFO : alphabet #6957
2020-12-19 00:54:28,609 : INFO : Computed distances or similarities (

...

2020-12-19 01:38:34,553 : INFO : token count processed
2020-12-19 01:38:34,559 : INFO : frequencies processed
2020-12-19 01:38:35,173 : INFO : scalar_distribution processed
2020-12-19 01:38:35,174 : INFO : entropies processed
2020-12-19 01:38:35,175 : INFO : extropies processed
2020-12-19 01:38:35,177 : INFO : token count processed
2020-12-19 01:38:35,179 : INFO : alphabet_source #6957
2020-12-19 01:38:35,180 : INFO : alphabet_target #6957
2020-12-19 01:38:35,181 : INFO : vocab #6957
2020-12-19 01:38:35,182 : INFO : diff #set()
2020-12-19 01:38:36,420 : INFO : alphabet #6957
2020-12-19 01:38:37,034 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ52.txt', 'test_data/LibEST_semeru_format/test/us2174.c')[[0.8640723963013043, 0.5364598510144787], [0.942912258207798, 0.05708774], [4.663532754804254, 1.4059345172710873], [7.366092813760617, 9.228957519717383, 9.521139417422694, 7.073910916055306, 2.1550466036620763, 0.29218189770531033]]
2020-12-19

2020-12-19 01:38:50,328 : INFO : extropies processed
2020-12-19 01:38:50,332 : INFO : token count processed
2020-12-19 01:38:50,334 : INFO : alphabet_source #6957
2020-12-19 01:38:50,336 : INFO : alphabet_target #6957
2020-12-19 01:38:50,337 : INFO : vocab #6957
2020-12-19 01:38:50,340 : INFO : diff #set()
2020-12-19 01:38:51,702 : INFO : alphabet #6957
2020-12-19 01:38:52,319 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ6.txt', 'test_data/LibEST_semeru_format/test/us4020.c')[[1.0099217847917674, 0.49753179828517674], [0.8688268959522247, 0.1311731], [2.7401032600285835, 1.298908549047567], [4.138589126445727, 6.985394788721831, 7.036839862104712, 4.087144053062847, 2.8982507356589844, 0.0514450733828804]]
2020-12-19 01:38:52,323 : INFO : Removed 40 and 2273 OOV words from document 1 and 2 (respectively).
2020-12-19 01:38:52,324 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 01:38:52,325 : INFO : built Dictionary

2020-12-19 01:39:05,557 : INFO : vocab #6957
2020-12-19 01:39:05,560 : INFO : diff #set()
2020-12-19 01:39:06,809 : INFO : alphabet #6957
2020-12-19 01:39:07,424 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ6.txt', 'test_data/LibEST_semeru_format/test/us1005.c')[[1.058379187828052, 0.48581913668451626], [0.7665635943412781, 0.2334364], [2.817856113506615, 1.3155321013041552], [4.138589126445727, 7.278774046648788, 7.321368016846124, 4.0959951562483905, 3.182778890400397, 0.042593970197335906]]
2020-12-19 01:39:07,427 : INFO : Removed 40 and 2288 OOV words from document 1 and 2 (respectively).
2020-12-19 01:39:07,428 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 01:39:07,429 : INFO : built Dictionary(36 unique tokens: ['est', 'respond', 'use', '200', 'back']...) from 2 documents (total 369 corpus positions)
2020-12-19 01:39:07,441 : INFO : token count processed
2020-12-19 01:39:07,449 : INFO : frequencies process

2020-12-19 01:39:22,650 : INFO : Removed 40 and 954 OOV words from document 1 and 2 (respectively).
2020-12-19 01:39:22,651 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 01:39:22,652 : INFO : built Dictionary(32 unique tokens: ['est', 'respond', 'use', '200', '://']...) from 2 documents (total 91 corpus positions)
2020-12-19 01:39:22,665 : INFO : token count processed
2020-12-19 01:39:22,671 : INFO : frequencies processed
2020-12-19 01:39:23,285 : INFO : scalar_distribution processed
2020-12-19 01:39:23,286 : INFO : entropies processed
2020-12-19 01:39:23,287 : INFO : extropies processed
2020-12-19 01:39:23,291 : INFO : token count processed
2020-12-19 01:39:23,293 : INFO : alphabet_source #6957
2020-12-19 01:39:23,295 : INFO : alphabet_target #6957
2020-12-19 01:39:23,296 : INFO : vocab #6957
2020-12-19 01:39:23,300 : INFO : diff #set()
2020-12-19 01:39:24,560 : INFO : alphabet #6957
2020-12-19 01:39:25,173 : INFO : Computed distances or similarities ('test

Source  \
0  test_data/LibEST_semeru_format/requirements/RQ...   
1  test_data/LibEST_semeru_format/requirements/RQ...   
2  test_data/LibEST_semeru_format/requirements/RQ...   
3  test_data/LibEST_semeru_format/requirements/RQ...   
4  test_data/LibEST_semeru_format/requirements/RQ...   

                                         Target  DistanceMetric.WMD  \
0   test_data/LibEST_semeru_format/test/us903.c            0.929608   
1  test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2   test_data/LibEST_semeru_format/test/us899.c            0.837307   
3  test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4   test_data/LibEST_semeru_format/test/us897.c            0.901434   

   SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                  0.518240            0.739114                  0.260886   
1                  0.510262            0.697518                  0.302482   
2                  0.544275            0.710308                  0.289692   
3                  0.513550            0.847159                  0.152841   
4                  0.525919            0.773193                  0.226807   

   EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0             4.464656             1.390740                   6.024675   
1             4.228282             1.385062                   6.024675   
2             4.634286             1.398938                   6.024675   
3             4.011289             1.368943                   6.024675   
4             4.105223             1.381910                   6.024675   

   EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                   8.626714          8.716142          5.935246   
1                   7.287890          7.522528          5.790037   
2                   8.158197          8.269749          5.913122   
3                   6.985395          7.273151          5.736918   
4                   6.792407          7.049971          5.767110   

   EntropyMetric.Loss  EntropyMetric.Noise  
0            2.691468             0.089428  
1            1.497854             0.234638  
2            2.245075             0.111552  
3            1.248476             0.287756  
4            1.025296             0.257564

In [ ]:
word2vec.df_nonground_link.head()

Source  \
0  test_data/LibEST_semeru_format/requirements/RQ...   
1  test_data/LibEST_semeru_format/requirements/RQ...   
2  test_data/LibEST_semeru_format/requirements/RQ...   
3  test_data/LibEST_semeru_format/requirements/RQ...   
4  test_data/LibEST_semeru_format/requirements/RQ...   

                                         Target  DistanceMetric.WMD  \
0   test_data/LibEST_semeru_format/test/us903.c            0.929608   
1  test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2   test_data/LibEST_semeru_format/test/us899.c            0.837307   
3  test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4   test_data/LibEST_semeru_format/test/us897.c            0.901434   

   SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                  0.518240            0.739114                  0.260886   
1                  0.510262            0.697518                  0.302482   
2                  0.544275            0.710308                  0.289692   
3                  0.513550            0.847159                  0.152841   
4                  0.525919            0.773193                  0.226807   

   EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0             4.464656             1.390740                   6.024675   
1             4.228282             1.385062                   6.024675   
2             4.634286             1.398938                   6.024675   
3             4.011289             1.368943                   6.024675   
4             4.105223             1.381910                   6.024675   

   EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                   8.626714          8.716142          5.935246   
1                   7.287890          7.522528          5.790037   
2                   8.158197          8.269749          5.913122   
3                   6.985395          7.273151          5.736918   
4                   6.792407          7.049971          5.767110   

   EntropyMetric.Loss  EntropyMetric.Noise  
0            2.691468             0.089428  
1            1.497854             0.234638  
2            2.245075             0.111552  
3            1.248476             0.287756  
4            1.025296             0.257564

In [ ]:
#tst 
#df_mapping = pd.read_csv(parameters['path_mappings'], header = 0, sep = ',')
#ground_links = word2vec.ground_truth_processing(from_mappings='True') #<---- SACP
ground_links = word2vec.ground_truth_processing(path_to_ground_truth) #<---- LIBEST
ground_links

[('RQ4.txt', 'us1864.c'),
 ('RQ4.txt', 'us901.c'),
 ('RQ4.txt', 'us1005.c'),
 ('RQ4.txt', 'us3512.c'),
 ('RQ4.txt', 'us895.c'),
 ('RQ4.txt', 'us897.c'),
 ('RQ4.txt', 'us900.c'),
 ('RQ6.txt', 'us1005.c'),
 ('RQ6.txt', 'us1159.c'),
 ('RQ6.txt', 'us3496.c'),
 ('RQ6.txt', 'us3512.c'),
 ('RQ6.txt', 'us3612.c'),
 ('RQ6.txt', 'us4020.c'),
 ('RQ6.txt', 'us748.c'),
 ('RQ6.txt', 'us893.c'),
 ('RQ6.txt', 'us895.c'),
 ('RQ6.txt', 'us896.c'),
 ('RQ6.txt', 'us897.c'),
 ('RQ6.txt', 'us898.c'),
 ('RQ6.txt', 'us899.c'),
 ('RQ6.txt', 'us900.c'),
 ('RQ8.txt', 'us1005.c'),
 ('RQ8.txt', 'us1159.c'),
 ('RQ8.txt', 'us1883.c'),
 ('RQ8.txt', 'us2174.c'),
 ('RQ8.txt', 'us3496.c'),
 ('RQ8.txt', 'us3512.c'),
 ('RQ8.txt', 'us3612.c'),
 ('RQ8.txt', 'us4020.c'),
 ('RQ8.txt', 'us748.c'),
 ('RQ8.txt', 'us893.c'),
 ('RQ8.txt', 'us895.c'),
 ('RQ8.txt', 'us896.c'),
 ('RQ8.txt', 'us897.c'),
 ('RQ8.txt', 'us898.c'),
 ('RQ8.txt', 'us899.c'),
 ('RQ8.txt', 'us900.c'),
 ('RQ11.txt', 'us1159.c'),
 ('RQ11.txt', 'us1883.c'),
 ('R

In [ ]:
len(ground_links)

352

In [ ]:
#tst
df_x = word2vec.df_nonground_link
df_x.head()

Source  \
0  test_data/LibEST_semeru_format/requirements/RQ...   
1  test_data/LibEST_semeru_format/requirements/RQ...   
2  test_data/LibEST_semeru_format/requirements/RQ...   
3  test_data/LibEST_semeru_format/requirements/RQ...   
4  test_data/LibEST_semeru_format/requirements/RQ...   

                                         Target  DistanceMetric.WMD  \
0   test_data/LibEST_semeru_format/test/us903.c            0.929608   
1  test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2   test_data/LibEST_semeru_format/test/us899.c            0.837307   
3  test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4   test_data/LibEST_semeru_format/test/us897.c            0.901434   

   SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                  0.518240            0.739114                  0.260886   
1                  0.510262            0.697518                  0.302482   
2                  0.544275            0.710308                  0.289692   
3                  0.513550            0.847159                  0.152841   
4                  0.525919            0.773193                  0.226807   

   EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0             4.464656             1.390740                   6.024675   
1             4.228282             1.385062                   6.024675   
2             4.634286             1.398938                   6.024675   
3             4.011289             1.368943                   6.024675   
4             4.105223             1.381910                   6.024675   

   EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                   8.626714          8.716142          5.935246   
1                   7.287890          7.522528          5.790037   
2                   8.158197          8.269749          5.913122   
3                   6.985395          7.273151          5.736918   
4                   6.792407          7.049971          5.767110   

   EntropyMetric.Loss  EntropyMetric.Noise  
0            2.691468             0.089428  
1            1.497854             0.234638  
2            2.245075             0.111552  
3            1.248476             0.287756  
4            1.025296             0.257564

In [ ]:
df_x['Source'].values

array(['test_data/LibEST_semeru_format/requirements/RQ17.txt',
       'test_data/LibEST_semeru_format/requirements/RQ17.txt',
       'test_data/LibEST_semeru_format/requirements/RQ17.txt', ...,
       'test_data/LibEST_semeru_format/requirements/RQ6.txt',
       'test_data/LibEST_semeru_format/requirements/RQ6.txt',
       'test_data/LibEST_semeru_format/requirements/RQ6.txt'],
      dtype=object)

In [ ]:
#tst
test_source = 'RQ50.txt'
test_target = 'us893.c'
df_x[( df_x["Source"].str.contains(test_source) ) & (df_x["Target"].str.contains(test_target, regex=False))]

Source  \
859  test_data/LibEST_semeru_format/requirements/RQ...   

                                          Target  DistanceMetric.WMD  \
859  test_data/LibEST_semeru_format/test/us893.c            0.983646   

     SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
859                  0.504122            0.849104                  0.150896   

     EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
859             4.892534             1.415386                   6.329472   

     EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
859                   7.905577          8.075343          6.159706   

     EntropyMetric.Loss  EntropyMetric.Noise  
859            1.745871             0.169766

In [ ]:
ground_links[0][0]

'RQ4.txt'

In [ ]:
ground_links[0][1]

'us1864.c'

In [ ]:
#tst
df_x[( df_x["Source"].str.contains(ground_links[0][0]) ) & (df_x["Target"].str.contains(ground_links[0][1], regex=False))]

Source  \
394  test_data/LibEST_semeru_format/requirements/RQ...   

                                           Target  DistanceMetric.WMD  \
394  test_data/LibEST_semeru_format/test/us1864.c            0.859013   

     SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
394                   0.53792            0.720722                  0.279278   

     EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
394             3.347434             1.307874                   5.492329   

     EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
394                   8.610843          8.658847          5.444325   

     EntropyMetric.Loss  EntropyMetric.Noise  
394            3.166518             0.048003

In [ ]:
def find_index_gt( tuple_g ):
    dist = df_x.loc[(df_x["Source"].str.eq(tuple_g[0]) ) & 
                 (df_x["Target"].str.contains(tuple_g[1], regex=False))]
    return dist.index.values
#dist

In [ ]:
#Formatted for SACP
matchGT = [ word2vec.findDistInDF( g , from_mappings=True ) for g in word2vec.ground_truth_processing(from_mappings=True)]
matchGT

KeyError: 'id_pr'

In [ ]:
matchGT = functools.reduce(lambda a,b : np.concatenate([a,b]), matchGT) #Concatenate indexes
matchGT

In [ ]:
new_column = pd.Series(np.full([len(matchGT)], 1 ), name=word2vec.params['names'][2], index = matchGT)

In [ ]:
new_column

In [ ]:
#Some of the mappings are not found in the non-ling list because the mappings have all the ground truth of the issues
#it might include files not take into account in the non-links part
matchGT_ = [ (g,word2vec.findDistInDF( g , from_mappings=True )) for g in word2vec.ground_truth_processing(from_mappings=True)]

In [ ]:
matchGT_

In [ ]:
len(matchGT)

In [ ]:
#[step 3]Saving Non-GroundTruth Links
word2vec.SaveLinks()

2020-12-19 01:48:50,778 : INFO : Saving in...../dvc-ds4se/metrics/traceability/experiments0.0.x/[libest-VectorizationType.word2vec-LinkType.req2tc-False-1608342530.750395].csv


In [ ]:
#Loading Non-GroundTruth Links (change the timestamp with the assigned in the previous step)
df_nonglinks = LoadLinks(timestamp=1608342530.750395, params=parameters)
df_nonglinks.head()

2020-12-19 01:49:02,982 : INFO : Loading computed links from... ../dvc-ds4se/metrics/traceability/experiments0.0.x/[libest-VectorizationType.word2vec-LinkType.req2tc-False-1608342530.750395].csv


Source  \
0  test_data/LibEST_semeru_format/requirements/RQ...   
1  test_data/LibEST_semeru_format/requirements/RQ...   
2  test_data/LibEST_semeru_format/requirements/RQ...   
3  test_data/LibEST_semeru_format/requirements/RQ...   
4  test_data/LibEST_semeru_format/requirements/RQ...   

                                         Target  DistanceMetric.WMD  \
0   test_data/LibEST_semeru_format/test/us903.c            0.929608   
1  test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2   test_data/LibEST_semeru_format/test/us899.c            0.837307   
3  test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4   test_data/LibEST_semeru_format/test/us897.c            0.901434   

   SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                  0.518240            0.739114                  0.260886   
1                  0.510262            0.697518                  0.302482   
2                  0.544275            0.710308                  0.289692   
3                  0.513550            0.847159                  0.152841   
4                  0.525919            0.773193                  0.226807   

   EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0             4.464656             1.390740                   6.024675   
1             4.228282             1.385062                   6.024675   
2             4.634286             1.398938                   6.024675   
3             4.011289             1.368943                   6.024675   
4             4.105223             1.381910                   6.024675   

   EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                   8.626714          8.716142          5.935246   
1                   7.287890          7.522528          5.790037   
2                   8.158197          8.269749          5.913122   
3                   6.985395          7.273151          5.736918   
4                   6.792407          7.049971          5.767110   

   EntropyMetric.Loss  EntropyMetric.Noise  
0            2.691468             0.089428  
1            1.497854             0.234638  
2            2.245075             0.111552  
3            1.248476             0.287756  
4            1.025296             0.257564

In [ ]:
#[step 4]GroundTruthMatching Testing
word2vec.MatchWithGroundTruth(path_to_ground_truth, semeru_format=True)
word2vec.df_ground_link

2020-12-19 01:49:09,020 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,024 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,028 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,030 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,033 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,036 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,038 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,041 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,043 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,046 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,049 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,051 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,054 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,057 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,062 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,066 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,069 

2020-12-19 01:49:09,453 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,459 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,464 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,466 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,469 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,472 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,474 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,485 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,487 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,490 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,493 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,498 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,502 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,504 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,507 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,510 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,513 

2020-12-19 01:49:09,895 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,899 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,902 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,905 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,907 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,910 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,913 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,916 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,918 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,921 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,924 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,926 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,930 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,935 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,938 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,941 : INFO : findDistInDF: semeru_format
2020-12-19 01:49:09,944 

Source  \
0     test_data/LibEST_semeru_format/requirements/RQ...   
1     test_data/LibEST_semeru_format/requirements/RQ...   
2     test_data/LibEST_semeru_format/requirements/RQ...   
3     test_data/LibEST_semeru_format/requirements/RQ...   
4     test_data/LibEST_semeru_format/requirements/RQ...   
...                                                 ...   
1087  test_data/LibEST_semeru_format/requirements/RQ...   
1088  test_data/LibEST_semeru_format/requirements/RQ...   
1089  test_data/LibEST_semeru_format/requirements/RQ...   
1090  test_data/LibEST_semeru_format/requirements/RQ...   
1091  test_data/LibEST_semeru_format/requirements/RQ...   

                                            Target  DistanceMetric.WMD  \
0      test_data/LibEST_semeru_format/test/us903.c            0.929608   
1     test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2      test_data/LibEST_semeru_format/test/us899.c            0.837307   
3     test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4      test_data/LibEST_semeru_format/test/us897.c            0.901434   
...                                            ...                 ...   
1087  test_data/LibEST_semeru_format/test/us1864.c            0.845571   
1088  test_data/LibEST_semeru_format/test/us1159.c            1.051327   
1089  test_data/LibEST_semeru_format/test/us2174.c            0.926151   
1090   test_data/LibEST_semeru_format/test/us893.c            0.997642   
1091   test_data/LibEST_semeru_format/test/us895.c            1.043785   

      SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                     0.518240            0.739114                  0.260886   
1                     0.510262            0.697518                  0.302482   
2                     0.544275            0.710308                  0.289692   
3                     0.513550            0.847159                  0.152841   
4                     0.525919            0.773193                  0.226807   
...                        ...                 ...                       ...   
1087                  0.541838            0.771328                  0.228672   
1088                  0.487489            0.842482                  0.157518   
1089                  0.519170            0.772877                  0.227123   
1090                  0.500590            0.826657                  0.173343   
1091                  0.489288            0.951820                  0.048180   

      EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0                4.464656             1.390740                   6.024675   
1                4.228282             1.385062                   6.024675   
2                4.634286             1.398938                   6.024675   
3                4.011289             1.368943                   6.024675   
4                4.105223             1.381910                   6.024675   
...                   ...                  ...                        ...   
1087             3.082328             1.324060                   4.138589   
1088             2.757004             1.314602                   4.138589   
1089             2.939884             1.321355                   4.138589   
1090             3.345074             1.351139                   4.138589   
1091             1.985228             1.197258                   4.138589   

      EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                      8.626714          8.716142          5.935246   
1                      7.287890          7.522528          5.790037   
2                      8.158197          8.269749          5.913122   
3                      6.985395          7.273151          5.736918   
4                      6.792407          7.049971          5.767110   
...                         ...               ...               ...   
1087                   8.610843          8.614900          4.134532 

In [ ]:
#[step 4.1]GroundTruthMatching Testing For CISCO Mappings <----- Warning SACP
word2vec.MatchWithGroundTruth(from_mappings=True)
word2vec.df_ground_link

In [ ]:
df_z = word2vec.df_ground_link
df_z[~df_z.isin([np.nan, np.inf, -np.inf]).any(1)]

Source  \
0     test_data/LibEST_semeru_format/requirements/RQ...   
1     test_data/LibEST_semeru_format/requirements/RQ...   
2     test_data/LibEST_semeru_format/requirements/RQ...   
3     test_data/LibEST_semeru_format/requirements/RQ...   
4     test_data/LibEST_semeru_format/requirements/RQ...   
...                                                 ...   
1087  test_data/LibEST_semeru_format/requirements/RQ...   
1088  test_data/LibEST_semeru_format/requirements/RQ...   
1089  test_data/LibEST_semeru_format/requirements/RQ...   
1090  test_data/LibEST_semeru_format/requirements/RQ...   
1091  test_data/LibEST_semeru_format/requirements/RQ...   

                                            Target  DistanceMetric.WMD  \
0      test_data/LibEST_semeru_format/test/us903.c            0.929608   
1     test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2      test_data/LibEST_semeru_format/test/us899.c            0.837307   
3     test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4      test_data/LibEST_semeru_format/test/us897.c            0.901434   
...                                            ...                 ...   
1087  test_data/LibEST_semeru_format/test/us1864.c            0.845571   
1088  test_data/LibEST_semeru_format/test/us1159.c            1.051327   
1089  test_data/LibEST_semeru_format/test/us2174.c            0.926151   
1090   test_data/LibEST_semeru_format/test/us893.c            0.997642   
1091   test_data/LibEST_semeru_format/test/us895.c            1.043785   

      SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                     0.518240            0.739114                  0.260886   
1                     0.510262            0.697518                  0.302482   
2                     0.544275            0.710308                  0.289692   
3                     0.513550            0.847159                  0.152841   
4                     0.525919            0.773193                  0.226807   
...                        ...                 ...                       ...   
1087                  0.541838            0.771328                  0.228672   
1088                  0.487489            0.842482                  0.157518   
1089                  0.519170            0.772877                  0.227123   
1090                  0.500590            0.826657                  0.173343   
1091                  0.489288            0.951820                  0.048180   

      EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0                4.464656             1.390740                   6.024675   
1                4.228282             1.385062                   6.024675   
2                4.634286             1.398938                   6.024675   
3                4.011289             1.368943                   6.024675   
4                4.105223             1.381910                   6.024675   
...                   ...                  ...                        ...   
1087             3.082328             1.324060                   4.138589   
1088             2.757004             1.314602                   4.138589   
1089             2.939884             1.321355                   4.138589   
1090             3.345074             1.351139                   4.138589   
1091             1.985228             1.197258                   4.138589   

      EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                      8.626714          8.716142          5.935246   
1                      7.287890          7.522528          5.790037   
2                      8.158197          8.269749          5.913122   
3                      6.985395          7.273151          5.736918   
4                      6.792407          7.049971          5.767110   
...                         ...               ...               ...   
1087                   8.610843          8.614900          4.134532 

In [ ]:
#debug
df_y = word2vec.df_ground_link.copy()
df_y

Source  \
0     test_data/LibEST_semeru_format/requirements/RQ...   
1     test_data/LibEST_semeru_format/requirements/RQ...   
2     test_data/LibEST_semeru_format/requirements/RQ...   
3     test_data/LibEST_semeru_format/requirements/RQ...   
4     test_data/LibEST_semeru_format/requirements/RQ...   
...                                                 ...   
1087  test_data/LibEST_semeru_format/requirements/RQ...   
1088  test_data/LibEST_semeru_format/requirements/RQ...   
1089  test_data/LibEST_semeru_format/requirements/RQ...   
1090  test_data/LibEST_semeru_format/requirements/RQ...   
1091  test_data/LibEST_semeru_format/requirements/RQ...   

                                            Target  DistanceMetric.WMD  \
0      test_data/LibEST_semeru_format/test/us903.c            0.929608   
1     test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2      test_data/LibEST_semeru_format/test/us899.c            0.837307   
3     test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4      test_data/LibEST_semeru_format/test/us897.c            0.901434   
...                                            ...                 ...   
1087  test_data/LibEST_semeru_format/test/us1864.c            0.845571   
1088  test_data/LibEST_semeru_format/test/us1159.c            1.051327   
1089  test_data/LibEST_semeru_format/test/us2174.c            0.926151   
1090   test_data/LibEST_semeru_format/test/us893.c            0.997642   
1091   test_data/LibEST_semeru_format/test/us895.c            1.043785   

      SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                     0.518240            0.739114                  0.260886   
1                     0.510262            0.697518                  0.302482   
2                     0.544275            0.710308                  0.289692   
3                     0.513550            0.847159                  0.152841   
4                     0.525919            0.773193                  0.226807   
...                        ...                 ...                       ...   
1087                  0.541838            0.771328                  0.228672   
1088                  0.487489            0.842482                  0.157518   
1089                  0.519170            0.772877                  0.227123   
1090                  0.500590            0.826657                  0.173343   
1091                  0.489288            0.951820                  0.048180   

      EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0                4.464656             1.390740                   6.024675   
1                4.228282             1.385062                   6.024675   
2                4.634286             1.398938                   6.024675   
3                4.011289             1.368943                   6.024675   
4                4.105223             1.381910                   6.024675   
...                   ...                  ...                        ...   
1087             3.082328             1.324060                   4.138589   
1088             2.757004             1.314602                   4.138589   
1089             2.939884             1.321355                   4.138589   
1090             3.345074             1.351139                   4.138589   
1091             1.985228             1.197258                   4.138589   

      EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                      8.626714          8.716142          5.935246   
1                      7.287890          7.522528          5.790037   
2                      8.158197          8.269749          5.913122   
3                      6.985395          7.273151          5.736918   
4                      6.792407          7.049971          5.767110   
...                         ...               ...               ...   
1087                   8.610843          8.614900          4.134532 

In [ ]:
#debug
df_y.update(new_column)

In [ ]:
new_column

In [ ]:
word2vec.df_ground_link[word2vec.df_ground_link['Linked?'] == 1]

Source  \
44    test_data/LibEST_semeru_format/requirements/RQ...   
45    test_data/LibEST_semeru_format/requirements/RQ...   
47    test_data/LibEST_semeru_format/requirements/RQ...   
58    test_data/LibEST_semeru_format/requirements/RQ...   
59    test_data/LibEST_semeru_format/requirements/RQ...   
...                                                 ...   
1084  test_data/LibEST_semeru_format/requirements/RQ...   
1085  test_data/LibEST_semeru_format/requirements/RQ...   
1088  test_data/LibEST_semeru_format/requirements/RQ...   
1090  test_data/LibEST_semeru_format/requirements/RQ...   
1091  test_data/LibEST_semeru_format/requirements/RQ...   

                                            Target  DistanceMetric.WMD  \
44     test_data/LibEST_semeru_format/test/us899.c            0.819607   
45    test_data/LibEST_semeru_format/test/us4020.c            0.942675   
47    test_data/LibEST_semeru_format/test/us1060.c            0.855173   
58    test_data/LibEST_semeru_format/test/us1864.c            0.718124   
59    test_data/LibEST_semeru_format/test/us1159.c            0.983724   
...                                            ...                 ...   
1084   test_data/LibEST_semeru_format/test/us748.c            0.871661   
1085  test_data/LibEST_semeru_format/test/us3612.c            1.083496   
1088  test_data/LibEST_semeru_format/test/us1159.c            1.051327   
1090   test_data/LibEST_semeru_format/test/us893.c            0.997642   
1091   test_data/LibEST_semeru_format/test/us895.c            1.043785   

      SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
44                    0.549569            0.749672                  0.250328   
45                    0.514754            0.846516                  0.153484   
47                    0.539033            0.831881                  0.168119   
58                    0.582030            0.784647                  0.215353   
59                    0.504102            0.824537                  0.175463   
...                        ...                 ...                       ...   
1084                  0.534285            0.785632                  0.214368   
1085                  0.479962            0.859709                  0.140291   
1088                  0.487489            0.842482                  0.157518   
1090                  0.500590            0.826657                  0.173343   
1091                  0.489288            0.951820                  0.048180   

      EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
44               4.280310             1.382068                   5.622179   
45               3.868299             1.366060                   5.622179   
47               4.250213             1.388677                   5.622179   
58               4.401750             1.392002                   5.622179   
59               3.956365             1.368030                   5.622179   
...                   ...                  ...                        ...   
1084             3.210587             1.341541                   4.138589   
1085             2.812879             1.312220                   4.138589   
1088             2.757004             1.314602                   4.138589   
1090             3.345074             1.351139                   4.138589   
1091             1.985228             1.197258                   4.138589   

      EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
44                     8.158197          8.235031          5.545345   
45                     6.985395          7.193951          5.413622   
47                     7.587626          7.746308          5.463497   
58                     8.610843          8.618406          5.614617   
59                     7.330886          7.501689          5.451376   
...                         ...               ...               ...   
1084                   8.675328          8.681645          4.132272 

In [ ]:
word2vec.df_ground_link[word2vec.df_ground_link['Linked?'] == 1].shape #Positive Links

In [ ]:
#[optional]GroundTruth Direct Processing
ground_links = word2vec.ground_truth_processing(path_to_ground_truth)
ground_links[141] # A tuple

('RQ33.txt', 'us894.c')

In [ ]:
#Inspecting Source
ground_links[141][0][:ground_links[141][0].find('.')] + '-'

'RQ33-'

In [ ]:
#Inspecting Target
ground_links[141][1][:ground_links[141][1].find('.')]

'us894'

In [ ]:
#[step 5]Saving GroundTruth Links
word2vec.SaveLinks(grtruth = True)

2020-12-19 01:49:53,525 : INFO : Saving in...../dvc-ds4se/metrics/traceability/experiments0.0.x/[libest-VectorizationType.word2vec-LinkType.req2tc-True-1608342593.495168].csv


In [ ]:
#Loading Non-GroundTruth Links (change the timestamp with the assigned in the previous step)
df_glinks = LoadLinks(timestamp=1608342593.495168, params=parameters,grtruth = True)
df_glinks.head()

2020-12-19 01:50:04,684 : INFO : Loading computed links from... ../dvc-ds4se/metrics/traceability/experiments0.0.x/[libest-VectorizationType.word2vec-LinkType.req2tc-True-1608342593.495168].csv


Source  \
0  test_data/LibEST_semeru_format/requirements/RQ...   
1  test_data/LibEST_semeru_format/requirements/RQ...   
2  test_data/LibEST_semeru_format/requirements/RQ...   
3  test_data/LibEST_semeru_format/requirements/RQ...   
4  test_data/LibEST_semeru_format/requirements/RQ...   

                                         Target  DistanceMetric.WMD  \
0   test_data/LibEST_semeru_format/test/us903.c            0.929608   
1  test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2   test_data/LibEST_semeru_format/test/us899.c            0.837307   
3  test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4   test_data/LibEST_semeru_format/test/us897.c            0.901434   

   SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                  0.518240            0.739114                  0.260886   
1                  0.510262            0.697518                  0.302482   
2                  0.544275            0.710308                  0.289692   
3                  0.513550            0.847159                  0.152841   
4                  0.525919            0.773193                  0.226807   

   EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0             4.464656             1.390740                   6.024675   
1             4.228282             1.385062                   6.024675   
2             4.634286             1.398938                   6.024675   
3             4.011289             1.368943                   6.024675   
4             4.105223             1.381910                   6.024675   

   EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                   8.626714          8.716142          5.935246   
1                   7.287890          7.522528          5.790037   
2                   8.158197          8.269749          5.913122   
3                   6.985395          7.273151          5.736918   
4                   6.792407          7.049971          5.767110   

   EntropyMetric.Loss  EntropyMetric.Noise  Linked?  
0            2.691468             0.089428      0.0  
1            1.497854             0.234638      0.0  
2            2.245075             0.111552      0.0  
3            1.248476             0.287756      0.0  
4            1.025296             0.257564      0.0

In [ ]:
df_glinks[df_glinks["Linked?"] == 0]

Source  \
0     test_data/LibEST_semeru_format/requirements/RQ...   
1     test_data/LibEST_semeru_format/requirements/RQ...   
2     test_data/LibEST_semeru_format/requirements/RQ...   
3     test_data/LibEST_semeru_format/requirements/RQ...   
4     test_data/LibEST_semeru_format/requirements/RQ...   
...                                                 ...   
1079  test_data/LibEST_semeru_format/requirements/RQ...   
1083  test_data/LibEST_semeru_format/requirements/RQ...   
1086  test_data/LibEST_semeru_format/requirements/RQ...   
1087  test_data/LibEST_semeru_format/requirements/RQ...   
1089  test_data/LibEST_semeru_format/requirements/RQ...   

                                            Target  DistanceMetric.WMD  \
0      test_data/LibEST_semeru_format/test/us903.c            0.929608   
1     test_data/LibEST_semeru_format/test/us3496.c            0.959776   
2      test_data/LibEST_semeru_format/test/us899.c            0.837307   
3     test_data/LibEST_semeru_format/test/us4020.c            0.947232   
4      test_data/LibEST_semeru_format/test/us897.c            0.901434   
...                                            ...                 ...   
1079   test_data/LibEST_semeru_format/test/us894.c            0.908948   
1083  test_data/LibEST_semeru_format/test/us1883.c            1.047163   
1086   test_data/LibEST_semeru_format/test/us901.c            0.857670   
1087  test_data/LibEST_semeru_format/test/us1864.c            0.845571   
1089  test_data/LibEST_semeru_format/test/us2174.c            0.926151   

      SimilarityMetric.WMD_sim  DistanceMetric.SCM  SimilarityMetric.SCM_sim  \
0                     0.518240            0.739114                  0.260886   
1                     0.510262            0.697518                  0.302482   
2                     0.544275            0.710308                  0.289692   
3                     0.513550            0.847159                  0.152841   
4                     0.525919            0.773193                  0.226807   
...                        ...                 ...                       ...   
1079                  0.523849            0.745993                  0.254007   
1083                  0.488481            0.740980                  0.259020   
1086                  0.538309            0.705430                  0.294570   
1087                  0.541838            0.771328                  0.228672   
1089                  0.519170            0.772877                  0.227123   

      EntropyMetric.MSI_I  EntropyMetric.MSI_X  EntropyMetric.Entropy_src  \
0                4.464656             1.390740                   6.024675   
1                4.228282             1.385062                   6.024675   
2                4.634286             1.398938                   6.024675   
3                4.011289             1.368943                   6.024675   
4                4.105223             1.381910                   6.024675   
...                   ...                  ...                        ...   
1079             3.202828             1.343610                   4.138589   
1083             3.115590             1.337921                   4.138589   
1086             3.185374             1.340750                   4.138589   
1087             3.082328             1.324060                   4.138589   
1089             2.939884             1.321355                   4.138589   

      EntropyMetric.Entropy_tgt  EntropyMetric.JI  EntropyMetric.MI  \
0                      8.626714          8.716142          5.935246   
1                      7.287890          7.522528          5.790037   
2                      8.158197          8.269749          5.913122   
3                      6.985395          7.273151          5.736918   
4                      6.792407          7.049971          5.767110   
...                         ...               ...               ...   
1079                   7.749662          7.762332          4.125919 

## 3. Artifacts Similarity with Doc2Vec

Try to reproduce the same empirical evaluation like here: [link](https://arxiv.org/pdf/1507.07998.pdf). Pay attention to:
- Accuracy vs. Dimensionality (we can replace accuracy for false positive rate or true positive rate)
- Visualize paragraph vectors using t-sne
- Computing Cosine Distance and Similarity. More about similarity [link](https://www.kdnuggets.com/2017/08/comparing-distance-measurements-python-scipy.html)

In [ ]:
#experiment 0.0.1

In [ ]:
path_to_trained_model = path_data+'/models/pv/bpe8k/[doc2vec-Py-Java-PVDBOW-500-20E-8k-1594572857.17191].model'

In [ ]:
def doc2vec_params():
    return {
        "vectorizationType": VectorizationType.doc2vec,
        "linkType": LinkType.req2tc,
        "system": 'libest',
        "system_path_config": {
            "system_path": path_data + 'se-benchmarking/traceability/cisco/libest_data/[libest-all-corpus-1596063103.098236].csv',
            "sep": '~',
            "names": ['ids','conv'],
            "prep": Preprocessing.conv
        },
        "source_type": SoftwareArtifacts.REQ.value,
        "target_type": SoftwareArtifacts.TC.value,
        "path_to_trained_model": path_to_trained_model,
        "saving_path":  path_data + 'metrics/traceability/experiments0.0.x/',
        "names": ['Source','Target','Linked?'],
        "model_prefix":path_model_prefix, #For BPE Analysis
    }

In [ ]:
doc2vec_params = doc2vec_params()
doc2vec_params

{'vectorizationType': <VectorizationType.doc2vec: 2>,
 'linkType': <LinkType.req2tc: 1>,
 'system': 'libest',
 'system_path_config': {'system_path': '../dvc-ds4se/se-benchmarking/traceability/cisco/libest_data/[libest-all-corpus-1596063103.098236].csv',
  'sep': '~',
  'names': ['ids', 'conv'],
  'prep': <Preprocessing.conv: 1>},
 'source_type': 'req',
 'target_type': 'tc',
 'path_to_trained_model': '../dvc-ds4se//models/pv/bpe8k/[doc2vec-Py-Java-PVDBOW-500-20E-8k-1594572857.17191].model',
 'saving_path': '../dvc-ds4se/metrics/traceability/experiments0.0.x/',
 'names': ['Source', 'Target', 'Linked?'],
 'model_prefix': '../dvc-ds4se/models/bpe/sentencepiece/wiki_py_java_bpe_8k'}

In [ ]:
#Export
class Doc2VecSeqVect(BasicSequenceVectorization):
    
    def __init__(self, params):
        super().__init__(params)
        self.new_model = gensim.models.Doc2Vec.load( params['path_to_trained_model'] )
        self.new_model.init_sims(replace=True)  # Normalizes the vectors in the word2vec class.
        self.df_inferred_src = None
        self.df_inferred_trg = None
        
        self.dict_distance_dispatcher = {
            DistanceMetric.COS: self.cos_scipy,
            SimilarityMetric.Pearson: self.pearson_abs_scipy,
            DistanceMetric.EUC: self.euclidean_scipy,
            DistanceMetric.MAN: self.manhattan_scipy
        }
    
    def distance(self, metric_list, link):
        '''Iterate on the metrics'''
        ν_inferredSource = self.df_inferred_src[self.df_inferred_src['ids'].str.contains(link[0])]['inf-doc2vec'].values[0]
        w_inferredTarget = self.df_inferred_trg[self.df_inferred_trg['ids'].str.contains(link[1])]['inf-doc2vec'].values[0]
        
        dist = [ self.dict_distance_dispatcher[metric](ν_inferredSource,w_inferredTarget) for metric in metric_list]
        logging.info("Computed distances or similarities "+ str(link) + str(dist))    
        return functools.reduce(lambda a,b : a+b, dist) #Always return a list
    
    def computeDistanceMetric(self, links, metric_list):
        '''It is computed the cosine similarity'''
        
        metric_labels = [ self.dict_labels[metric] for metric in metric_list] #tracking of the labels
        distSim = [[link[0], link[1], self.distance( metric_list, link )] for link in links] #Return the link with metrics
        distSim = [[elem[0], elem[1]] + elem[2] for elem in distSim] #Return the link with metrics
        
        return distSim, functools.reduce(lambda a,b : a+b, metric_labels)

    
    def InferDoc2Vec(self, steps=200):
        '''Activate Inference on Target and Source Corpus'''
        self.df_inferred_src = self.df_source.copy()
        self.df_inferred_trg = self.df_target.copy()
        
        text = self.params['system_path_config']['names'][1]
        self.df_inferred_src['inf-doc2vec'] =  [self.new_model.infer_vector(artifact.split(),steps=steps) for artifact in self.df_inferred_src[text].values]
        self.df_inferred_trg['inf-doc2vec'] =  [self.new_model.infer_vector(artifact.split(),steps=steps) for artifact in self.df_inferred_trg[text].values]
        
        logging.info("Infer Doc2Vec on Source and Target Complete")

### Testing Doc2Vec SequenceVectorization

In [ ]:
doc2vec = Doc2VecSeqVect(params = doc2vec_params)

2020-12-19 03:33:52,739 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-12-19 03:33:52,794 : INFO : built Dictionary(6957 unique tokens: ['");', '"../../', '("\\', '();', ')))']...) from 87 documents (total 88944 corpus positions)
2020-12-19 03:33:52,795 : INFO : conventional preprocessing documents, dictionary, and vocab for the test corpus
2020-12-19 03:33:52,796 : INFO : loading Doc2Vec object from ../dvc-ds4se//models/pv/bpe8k/[doc2vec-Py-Java-PVDBOW-500-20E-8k-1594572857.17191].model
2020-12-19 03:33:52,968 : INFO : loading vocabulary recursively from ../dvc-ds4se//models/pv/bpe8k/[doc2vec-Py-Java-PVDBOW-500-20E-8k-1594572857.17191].model.vocabulary.* with mmap=None
2020-12-19 03:33:52,970 : INFO : loading trainables recursively from ../dvc-ds4se//models/pv/bpe8k/[doc2vec-Py-Java-PVDBOW-500-20E-8k-1594572857.17191].model.trainables.* with mmap=None
2020-12-19 03:33:52,971 : INFO : loading syn1neg from ../dvc-ds4se//models/pv/bpe8k/[doc2vec-Py-Java-PVDBOW-500-20

In [ ]:
doc2vec.df_source.head(2)

ids  \
35  test_data/LibEST_semeru_format/requirements/RQ...   
36  test_data/LibEST_semeru_format/requirements/RQ...   

                                                 conv  
35  requir http uri control est server must suppor...  
36  requir server side key generat respons request...

In [ ]:
#[step1]Apply Doc2Vec Inference
doc2vec.InferDoc2Vec( steps = 200 )

2020-12-19 03:34:15,393 : INFO : Infer Doc2Vec on Source and Target Complete


In [ ]:
doc2vec.df_inferred_src.head(2)

ids  \
35  test_data/LibEST_semeru_format/requirements/RQ...   
36  test_data/LibEST_semeru_format/requirements/RQ...   

                                                 conv  \
35  requir http uri control est server must suppor...   
36  requir server side key generat respons request...   

                                          inf-doc2vec  
35  [-1.627681, -1.1846577, 0.0467408, -0.09786891...  
36  [-1.2679539, 0.8652082, -0.66573286, -2.190202...

In [ ]:
len(doc2vec.df_inferred_src['inf-doc2vec'].values[35])

500

In [ ]:
len(doc2vec.df_inferred_src['inf-doc2vec'].values[36])

500

In [ ]:
#test_inferDoc2Vec_trg = inferDoc2Vec(df_target)
#test_inferDoc2Vec_trg.head()
doc2vec.df_inferred_trg.head(2)

ids  \
0   test_data/LibEST_semeru_format/test/us903.c   
1  test_data/LibEST_semeru_format/test/us3496.c   

                                                conv  \
0  unit test user stori server simpl enrol august...   
1  unit test uri path segment extens support marc...   

                                         inf-doc2vec  
0  [-1.0151138, -1.3879219, -2.6165612, -4.045337...  
1  [-2.4390655, -0.9076792, -1.7120461, -2.499704...

In [ ]:
#tst correlation
pearsonr(doc2vec.df_inferred_trg['inf-doc2vec'][0], doc2vec.df_inferred_trg['inf-doc2vec'][0])

(0.9999999999999999, 0.0)

In [ ]:
len(doc2vec.df_inferred_src['inf-doc2vec'])

52

In [ ]:
pearsonr(doc2vec.df_inferred_trg['inf-doc2vec'][0], doc2vec.df_inferred_src['inf-doc2vec'][35])

(0.532670673449515, 5.46237708290494e-38)

In [ ]:
#[step 2]NonGroundTruth Computation
metric_l = [DistanceMetric.EUC,DistanceMetric.COS,DistanceMetric.MAN, SimilarityMetric.Pearson]
doc2vec.ComputeDistanceArtifacts( sampling=False, samples = 50, metric_list = metric_l )
doc2vec.df_nonground_link.head()

2020-12-19 03:34:43,609 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ17.txt', 'test_data/LibEST_semeru_format/test/us903.c')[[44.1058349609375, 0.022170080675061637], [0.46729451417922974, 0.5327054858207703], [795.84357, 0.0012549514629291826], [0.532670673449515]]
2020-12-19 03:34:43,615 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ17.txt', 'test_data/LibEST_semeru_format/test/us3496.c')[[43.145660400390625, 0.02265228316736545], [0.38369375467300415, 0.6163062453269958], [746.00366, 0.001338681522894036], [0.6146666837799339]]
2020-12-19 03:34:43,620 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ17.txt', 'test_data/LibEST_semeru_format/test/us899.c')[[47.40620803833008, 0.020658507256097355], [0.389950692653656, 0.610049307346344], [850.88806, 0.0011738631460707324], [0.6097129258371485]]
2020-12-19 03:34:43,623 : INFO : Computed distances or si

2020-12-19 03:34:43,698 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ46.txt', 'test_data/LibEST_semeru_format/test/us900.c')[[50.58488464355469, 0.01938552362595902], [0.6353503465652466, 0.3646496534347534], [904.527, 0.001104329329555355], [0.3662752322148147]]
2020-12-19 03:34:43,701 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ46.txt', 'test_data/LibEST_semeru_format/test/us896.c')[[45.83034133911133, 0.021353677368241373], [0.6907251179218292, 0.3092748820781708], [820.71185, 0.0012169716139736923], [0.3099119313930767]]
2020-12-19 03:34:43,704 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ46.txt', 'test_data/LibEST_semeru_format/test/us894.c')[[54.74112319946289, 0.017940076241765357], [0.6133263409137726, 0.3866736590862274], [970.46674, 0.001029371323903838], [0.38779708281187525]]
2020-12-19 03:34:43,707 : INFO : Computed distances or simi

2020-12-19 03:34:43,776 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ18.txt', 'test_data/LibEST_semeru_format/test/us1883.c')[[53.88861846923828, 0.018218713239438498], [0.4194219708442688, 0.5805780291557312], [960.6216, 0.0010399101046460319], [0.5803437211183244]]
2020-12-19 03:34:43,779 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ18.txt', 'test_data/LibEST_semeru_format/test/us748.c')[[43.54933166503906, 0.02244702586155224], [0.43223053216934204, 0.567769467830658], [771.17303, 0.0012950465182068886], [0.5675710510263299]]
2020-12-19 03:34:43,781 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ18.txt', 'test_data/LibEST_semeru_format/test/us3612.c')[[42.812747955322266, 0.022824407202664914], [0.5435371696949005, 0.4564628303050995], [769.4116, 0.0012980074191771722], [0.4566375218074007]]
2020-12-19 03:34:43,784 : INFO : Computed distances or 

2020-12-19 03:34:43,851 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ48.txt', 'test_data/LibEST_semeru_format/test/us1159.c')[[48.700164794921875, 0.020120657630136776], [0.47075098752975464, 0.5292490124702454], [877.14, 0.0011387705642822222], [0.5282152014538007]]
2020-12-19 03:34:43,854 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ48.txt', 'test_data/LibEST_semeru_format/test/us2174.c')[[50.801265716552734, 0.019304547604528068], [0.4562833905220032, 0.5437166094779968], [909.79285, 0.00109794450367668], [0.5438230430654303]]
2020-12-19 03:34:43,857 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ48.txt', 'test_data/LibEST_semeru_format/test/us893.c')[[47.12606430053711, 0.02077876124993748], [0.5910617709159851, 0.4089382290840149], [852.8504, 0.0011711653431130595], [0.4081211586903623]]
2020-12-19 03:34:43,859 : INFO : Computed distances or si

2020-12-19 03:34:43,930 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ29.txt', 'test_data/LibEST_semeru_format/test/us899.c')[[54.751319885253906, 0.017936795076030077], [0.589832216501236, 0.41016778349876404], [966.4589, 0.0010336356158128332], [0.4095022400851886]]
2020-12-19 03:34:43,933 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ29.txt', 'test_data/LibEST_semeru_format/test/us4020.c')[[46.95840835571289, 0.020851400917705355], [0.5977496802806854, 0.4022503197193146], [837.5758, 0.0011924980344598741], [0.4012898968696515]]
2020-12-19 03:34:43,935 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ29.txt', 'test_data/LibEST_semeru_format/test/us897.c')[[50.391754150390625, 0.019458374529766835], [0.585319995880127, 0.41468000411987305], [870.6389, 0.0011472640581160949], [0.41426352687099677]]
2020-12-19 03:34:43,938 : INFO : Computed distances or

...

2020-12-19 03:34:46,594 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ19.txt', 'test_data/LibEST_semeru_format/test/us1060.c')[[39.837642669677734, 0.024487211666174544], [0.47759974002838135, 0.5224002599716187], [713.5393, 0.0013995031353858697], [0.5226751766284409]]
2020-12-19 03:34:46,596 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ19.txt', 'test_data/LibEST_semeru_format/test/us900.c')[[43.42311477661133, 0.022510803329047466], [0.4674469232559204, 0.5325530767440796], [771.498, 0.0012945017570664872], [0.5328871036724985]]
2020-12-19 03:34:46,599 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ19.txt', 'test_data/LibEST_semeru_format/test/us896.c')[[35.59723663330078, 0.027324467418670454], [0.47442901134490967, 0.5255709886550903], [622.0724, 0.001604949954047728], [0.5255861914449763]]
2020-12-19 03:34:46,602 : INFO : Computed distances or s

2020-12-19 03:34:46,670 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ1.txt', 'test_data/LibEST_semeru_format/test/us3512.c')[[57.67479705810547, 0.017043092607712015], [0.41819626092910767, 0.5818037390708923], [1038.9489, 0.0009615857525670361], [0.5814884070907771]]
2020-12-19 03:34:46,673 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ1.txt', 'test_data/LibEST_semeru_format/test/us1883.c')[[55.14423370361328, 0.01781126812201273], [0.4386489987373352, 0.5613510012626648], [973.61865, 0.0010260423372723405], [0.5597885845116074]]
2020-12-19 03:34:46,675 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ1.txt', 'test_data/LibEST_semeru_format/test/us748.c')[[43.254886627197266, 0.022596374687929726], [0.42891693115234375, 0.5710830688476562], [773.80817, 0.0012906420495181479], [0.5713928597943922]]
2020-12-19 03:34:46,681 : INFO : Computed distances or

2020-12-19 03:34:46,750 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ38.txt', 'test_data/LibEST_semeru_format/test/us1159.c')[[47.866050720214844, 0.02046410514583126], [0.5297326147556305, 0.4702673852443695], [867.5697, 0.0011513180779003287], [0.4693657404469805]]
2020-12-19 03:34:46,753 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ38.txt', 'test_data/LibEST_semeru_format/test/us2174.c')[[46.33984375, 0.0211238551035564], [0.43760108947753906, 0.5623989105224609], [832.69446, 0.0011994802057213975], [0.562286149166968]]
2020-12-19 03:34:46,756 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ38.txt', 'test_data/LibEST_semeru_format/test/us893.c')[[43.79230880737305, 0.022325261336727405], [0.4858347177505493, 0.5141652822494507], [790.09656, 0.0012640681979606098], [0.5136244102000073]]
2020-12-19 03:34:46,759 : INFO : Computed distances or similar

2020-12-19 03:34:46,825 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ6.txt', 'test_data/LibEST_semeru_format/test/us899.c')[[57.211307525634766, 0.017178792961481334], [0.6967165768146515, 0.3032834231853485], [1014.9628, 0.0009842879787282295], [0.30293800421038164]]
2020-12-19 03:34:46,828 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ6.txt', 'test_data/LibEST_semeru_format/test/us4020.c')[[48.801513671875, 0.020079710961973068], [0.6830730438232422, 0.3169269561767578], [883.09143, 0.001131104731157586], [0.31653041582066527]]
2020-12-19 03:34:46,831 : INFO : Computed distances or similarities ('test_data/LibEST_semeru_format/requirements/RQ6.txt', 'test_data/LibEST_semeru_format/test/us897.c')[[52.403560638427734, 0.018725343180215355], [0.6645509600639343, 0.3354490399360657], [924.5156, 0.0010804787871625614], [0.33520607133415975]]
2020-12-19 03:34:46,834 : INFO : Computed distances or s

Source  \
0  test_data/LibEST_semeru_format/requirements/RQ...   
1  test_data/LibEST_semeru_format/requirements/RQ...   
2  test_data/LibEST_semeru_format/requirements/RQ...   
3  test_data/LibEST_semeru_format/requirements/RQ...   
4  test_data/LibEST_semeru_format/requirements/RQ...   

                                         Target  DistanceMetric.EUC  \
0   test_data/LibEST_semeru_format/test/us903.c           44.105835   
1  test_data/LibEST_semeru_format/test/us3496.c           43.145660   
2   test_data/LibEST_semeru_format/test/us899.c           47.406208   
3  test_data/LibEST_semeru_format/test/us4020.c           39.962620   
4   test_data/LibEST_semeru_format/test/us897.c           43.581291   

   SimilarityMetric.EUC_sim  DistanceMetric.COS  SimilarityMetric.COS_sim  \
0                  0.022170            0.467295                  0.532705   
1                  0.022652            0.383694                  0.616306   
2                  0.020659            0.389951                  0.610049   
3                  0.024413            0.373937                  0.626063   
4                  0.022431            0.386722                  0.613278   

   DistanceMetric.MAN  SimilarityMetric.MAN_sim  SimilarityMetric.Pearson  
0          795.843567                  0.001255                  0.532671  
1          746.003662                  0.001339                  0.614667  
2          850.888062                  0.001174                  0.609713  
3          716.214722                  0.001394                  0.624889  
4          761.269653                  0.001312                  0.613646

In [ ]:
#[step 3]Saving Non-GroundTruth Links
doc2vec.SaveLinks()

2020-12-19 03:34:46,963 : INFO : Saving in...../dvc-ds4se/metrics/traceability/experiments0.0.x/[libest-VectorizationType.doc2vec-LinkType.req2tc-False-1608348886.946251].csv


In [ ]:
#Loading Non-GroundTruth Links (change the timestamp with the assigned in the previous step)
df_nonglinks_doc2vec = LoadLinks(timestamp=1608348886.946251, params=doc2vec_params)
df_nonglinks_doc2vec.head()

2020-12-19 03:36:41,779 : INFO : Loading computed links from... ../dvc-ds4se/metrics/traceability/experiments0.0.x/[libest-VectorizationType.doc2vec-LinkType.req2tc-False-1608348886.946251].csv


Source  \
0  test_data/LibEST_semeru_format/requirements/RQ...   
1  test_data/LibEST_semeru_format/requirements/RQ...   
2  test_data/LibEST_semeru_format/requirements/RQ...   
3  test_data/LibEST_semeru_format/requirements/RQ...   
4  test_data/LibEST_semeru_format/requirements/RQ...   

                                         Target  DistanceMetric.EUC  \
0   test_data/LibEST_semeru_format/test/us903.c           44.105835   
1  test_data/LibEST_semeru_format/test/us3496.c           43.145660   
2   test_data/LibEST_semeru_format/test/us899.c           47.406208   
3  test_data/LibEST_semeru_format/test/us4020.c           39.962620   
4   test_data/LibEST_semeru_format/test/us897.c           43.581291   

   SimilarityMetric.EUC_sim  DistanceMetric.COS  SimilarityMetric.COS_sim  \
0                  0.022170            0.467295                  0.532705   
1                  0.022652            0.383694                  0.616306   
2                  0.020659            0.389951                  0.610049   
3                  0.024413            0.373937                  0.626063   
4                  0.022431            0.386722                  0.613278   

   DistanceMetric.MAN  SimilarityMetric.MAN_sim  SimilarityMetric.Pearson  
0          795.843567                  0.001255                  0.532671  
1          746.003662                  0.001339                  0.614667  
2          850.888062                  0.001174                  0.609713  
3          716.214722                  0.001394                  0.624889  
4          761.269653                  0.001312                  0.613646

In [ ]:
#[step 4]GroundTruthMatching Testing
doc2vec.MatchWithGroundTruth(path_to_ground_truth)
doc2vec.df_ground_link

2020-12-19 03:36:50,514 : INFO : findDistInDF: default
2020-12-19 03:36:50,518 : INFO : findDistInDF: default
2020-12-19 03:36:50,524 : INFO : findDistInDF: default
2020-12-19 03:36:50,530 : INFO : findDistInDF: default
2020-12-19 03:36:50,534 : INFO : findDistInDF: default
2020-12-19 03:36:50,537 : INFO : findDistInDF: default
2020-12-19 03:36:50,540 : INFO : findDistInDF: default
2020-12-19 03:36:50,544 : INFO : findDistInDF: default
2020-12-19 03:36:50,548 : INFO : findDistInDF: default
2020-12-19 03:36:50,552 : INFO : findDistInDF: default
2020-12-19 03:36:50,556 : INFO : findDistInDF: default
2020-12-19 03:36:50,559 : INFO : findDistInDF: default
2020-12-19 03:36:50,563 : INFO : findDistInDF: default
2020-12-19 03:36:50,566 : INFO : findDistInDF: default
2020-12-19 03:36:50,570 : INFO : findDistInDF: default
2020-12-19 03:36:50,573 : INFO : findDistInDF: default
2020-12-19 03:36:50,577 : INFO : findDistInDF: default
2020-12-19 03:36:50,581 : INFO : findDistInDF: default
2020-12-19

2020-12-19 03:36:51,055 : INFO : findDistInDF: default
2020-12-19 03:36:51,058 : INFO : findDistInDF: default
2020-12-19 03:36:51,066 : INFO : findDistInDF: default
2020-12-19 03:36:51,070 : INFO : findDistInDF: default
2020-12-19 03:36:51,073 : INFO : findDistInDF: default
2020-12-19 03:36:51,077 : INFO : findDistInDF: default
2020-12-19 03:36:51,080 : INFO : findDistInDF: default
2020-12-19 03:36:51,084 : INFO : findDistInDF: default
2020-12-19 03:36:51,087 : INFO : findDistInDF: default
2020-12-19 03:36:51,090 : INFO : findDistInDF: default
2020-12-19 03:36:51,094 : INFO : findDistInDF: default
2020-12-19 03:36:51,097 : INFO : findDistInDF: default
2020-12-19 03:36:51,101 : INFO : findDistInDF: default
2020-12-19 03:36:51,107 : INFO : findDistInDF: default
2020-12-19 03:36:51,112 : INFO : findDistInDF: default
2020-12-19 03:36:51,115 : INFO : findDistInDF: default
2020-12-19 03:36:51,119 : INFO : findDistInDF: default
2020-12-19 03:36:51,122 : INFO : findDistInDF: default
2020-12-19

2020-12-19 03:36:51,637 : INFO : findDistInDF: default
2020-12-19 03:36:51,641 : INFO : findDistInDF: default
2020-12-19 03:36:51,644 : INFO : findDistInDF: default
2020-12-19 03:36:51,648 : INFO : findDistInDF: default
2020-12-19 03:36:51,651 : INFO : findDistInDF: default
2020-12-19 03:36:51,655 : INFO : findDistInDF: default
2020-12-19 03:36:51,658 : INFO : findDistInDF: default
2020-12-19 03:36:51,662 : INFO : findDistInDF: default
2020-12-19 03:36:51,665 : INFO : findDistInDF: default
2020-12-19 03:36:51,669 : INFO : findDistInDF: default
2020-12-19 03:36:51,672 : INFO : findDistInDF: default
2020-12-19 03:36:51,676 : INFO : findDistInDF: default
2020-12-19 03:36:51,679 : INFO : findDistInDF: default
2020-12-19 03:36:51,683 : INFO : findDistInDF: default
2020-12-19 03:36:51,686 : INFO : findDistInDF: default
2020-12-19 03:36:51,690 : INFO : findDistInDF: default
2020-12-19 03:36:51,693 : INFO : findDistInDF: default
2020-12-19 03:36:51,697 : INFO : findDistInDF: default
2020-12-19

Source  \
0     test_data/LibEST_semeru_format/requirements/RQ...   
1     test_data/LibEST_semeru_format/requirements/RQ...   
2     test_data/LibEST_semeru_format/requirements/RQ...   
3     test_data/LibEST_semeru_format/requirements/RQ...   
4     test_data/LibEST_semeru_format/requirements/RQ...   
...                                                 ...   
1087  test_data/LibEST_semeru_format/requirements/RQ...   
1088  test_data/LibEST_semeru_format/requirements/RQ...   
1089  test_data/LibEST_semeru_format/requirements/RQ...   
1090  test_data/LibEST_semeru_format/requirements/RQ...   
1091  test_data/LibEST_semeru_format/requirements/RQ...   

                                            Target  DistanceMetric.EUC  \
0      test_data/LibEST_semeru_format/test/us903.c           44.105835   
1     test_data/LibEST_semeru_format/test/us3496.c           43.145660   
2      test_data/LibEST_semeru_format/test/us899.c           47.406208   
3     test_data/LibEST_semeru_format/test/us4020.c           39.962620   
4      test_data/LibEST_semeru_format/test/us897.c           43.581291   
...                                            ...                 ...   
1087  test_data/LibEST_semeru_format/test/us1864.c           48.111172   
1088  test_data/LibEST_semeru_format/test/us1159.c           51.451206   
1089  test_data/LibEST_semeru_format/test/us2174.c           53.151047   
1090   test_data/LibEST_semeru_format/test/us893.c           46.669491   
1091   test_data/LibEST_semeru_format/test/us895.c           47.029556   

      SimilarityMetric.EUC_sim  DistanceMetric.COS  SimilarityMetric.COS_sim  \
0                     0.022170            0.467295                  0.532705   
1                     0.022652            0.383694                  0.616306   
2                     0.020659            0.389951                  0.610049   
3                     0.024413            0.373937                  0.626063   
4                     0.022431            0.386722                  0.613278   
...                        ...                 ...                       ...   
1087                  0.020362            0.642251                  0.357749   
1088                  0.019065            0.701924                  0.298076   
1089                  0.018467            0.655677                  0.344323   
1090                  0.020978            0.562637                  0.437363   
1091                  0.020821            0.691705                  0.308295   

      DistanceMetric.MAN  SimilarityMetric.MAN_sim  SimilarityMetric.Pearson  \
0             795.843567                  0.001255                  0.532671   
1             746.003662                  0.001339                  0.614667   
2             850.888062                  0.001174                  0.609713   
3             716.214722                  0.001394                  0.624889   
4             761.269653                  0.001312                  0.613646   
...                  ...                       ...                       ...   
1087          846.068726                  0.001181                  0.357422   
1088          931.417725                  0.001072                  0.297687   
1089          952.509399                  0.001049                  0.344142   
1090          841.761230                  0.001187                  0.437124   
1091          845.387817                  0.001181                  0.308178   

      Linked?  
0           0  
1           0  
2           0  
3           0  
4           0  
...       ...  
1087        0  
1088        0  
1089        0  
1090        0  
1091        0  

[1092 rows x 10 columns]

In [ ]:
#[step 5]Saving GroundTruth Links
doc2vec.SaveLinks(grtruth = True)

2020-12-19 03:36:55,474 : INFO : Saving in...../dvc-ds4se/metrics/traceability/experiments0.0.x/[libest-VectorizationType.doc2vec-LinkType.req2tc-True-1608349015.451968].csv


In [ ]:
#Loading Non-GroundTruth Links (change the timestamp with the assigned in the previous step)
df_glinks_doc2vec = LoadLinks(timestamp=1608349015.451968, params=doc2vec_params, grtruth = True)
df_glinks_doc2vec.head()

2020-12-19 03:37:11,312 : INFO : Loading computed links from... ../dvc-ds4se/metrics/traceability/experiments0.0.x/[libest-VectorizationType.doc2vec-LinkType.req2tc-True-1608349015.451968].csv


Source  \
0  test_data/LibEST_semeru_format/requirements/RQ...   
1  test_data/LibEST_semeru_format/requirements/RQ...   
2  test_data/LibEST_semeru_format/requirements/RQ...   
3  test_data/LibEST_semeru_format/requirements/RQ...   
4  test_data/LibEST_semeru_format/requirements/RQ...   

                                         Target  DistanceMetric.EUC  \
0   test_data/LibEST_semeru_format/test/us903.c           44.105835   
1  test_data/LibEST_semeru_format/test/us3496.c           43.145660   
2   test_data/LibEST_semeru_format/test/us899.c           47.406208   
3  test_data/LibEST_semeru_format/test/us4020.c           39.962620   
4   test_data/LibEST_semeru_format/test/us897.c           43.581291   

   SimilarityMetric.EUC_sim  DistanceMetric.COS  SimilarityMetric.COS_sim  \
0                  0.022170            0.467295                  0.532705   
1                  0.022652            0.383694                  0.616306   
2                  0.020659            0.389951                  0.610049   
3                  0.024413            0.373937                  0.626063   
4                  0.022431            0.386722                  0.613278   

   DistanceMetric.MAN  SimilarityMetric.MAN_sim  SimilarityMetric.Pearson  \
0          795.843567                  0.001255                  0.532671   
1          746.003662                  0.001339                  0.614667   
2          850.888062                  0.001174                  0.609713   
3          716.214722                  0.001394                  0.624889   
4          761.269653                  0.001312                  0.613646   

   Linked?  
0        0  
1        0  
2        0  
3        0  
4        0